**To make the assignment, first run the code below to import the right libraries.**

In [61]:
# =================================
# Imports
# =================================
from PyCh import *
from numpy import random
from dataclasses import dataclass
from matplotlib import pyplot
import math

#extra imports
import pandas as pd
import requests
import matplotlib.pyplot as plt
import statistics

<h1><center> 4DC10. Intermediate assignment</center></h1>
<h2><center> Modeling and simulation of an autonomous vehicle storage and retrieval system</center></h2>
    
# 1 Subject

Made by 
* Ben Gortemaker
* Wouter Kromhout

Today's competitive environment, in which deliveries need to be faster and order sizes become smaller, forces material handling providers to progressively develop new and better solutions. A recent development in automated material-handling technology for unit load storage and retrieval is the autonomous vehicle storage and retrieval system (AVS/RS). Figure 1 shows a representation of an AVS/RS for the handling of totes, while Figure 2 illustrates a single tier (floor, level). The storage racks are single-deep and double-sided. Each storage position is of the same size and can hold one tote. Lifts are mounted at fixed locations at one end of each storage aisle. The input/output (I/O) point is located at the first tier beside each lift. Autonomous vehicles are dedicated to a storage aisle within a specific tier (so-called tier-captive configuration). The first position on either side of the storage aisle in all tiers serves as a buffer and is used to manage the transfer of totes between vehicles and lifts (see Figure 2). One buffer (out) handles totes which have been retrieved, the other one (in), located on the other side of the storage aisle, handles the totes to be stored. The presence of these buffers allows the lift and vehicle to work independently of each other. 

The throughput performance of AVS/RS systems can be affected by design decisions (such as number of tiers, number of aisles, and depth of aisles) as well as operational decisions (such as tote storage location and order assignment).

Figure 1: AVS/RS with tier-captive configuration [1] | Figure 2: Single tier in AVS/RS [1]
- | - 
<img src="figures/avs.png" alt="drawing" width="400"/> | <img src="figures/avrs2.png" alt="drawing" width="400"/>




# 2 Goal
The goal of this assignment is to study this new material handling solution by using computer simulation. This study can be restricted to the retrieval process only, i.e., the vehicles perform only single retrieval cycles. Clearly, the retrieval phase is the most critical activity from an organisational viewpoint, as it is directly related to customer service level and &mdash; in contrast to the storage phase &mdash; it cannot be postponed to a period of low workload. 

The objectives of this assignment can be summarized as follows:
- Develop a simulation model of one aisle that consists of Level tiers with retrieval process to assess the system performance in terms of throughput and flow time.
- Systematically develop the model process by process, and verify and validate each process using analytical results.
- Investigate design trade-offs, i.e., via different layouts (number of columns and tiers), for this material handling system.

# 3 Description of the AVS/RS
The AVS/RS is a fully automated system that can store and retrieve unit loads. The unit loads are placed in totes, a type of box, and these totes are placed in a designated aisle and column for storage. When retrieved, an autonomous vehicle places the totes in a buffer at the end of the aisle. There is one autonomous vehicle for every aisle within the tier. This is called the tier-captive configuration. From the buffer, the totes are picked by a lift that serves all tiers inone aisle, see Figure 2. In this assignment only one aisle that consists of `Level` tiers has to be modelled. Each aisle has depth number of columns of width `dv` metres and height `dl` metres.

Requests for a tote arrive for each tier, asking for a tote with a random (uniformly distributed) column assigned to it. The inter arrival time of requests is exponentially distributed with mean value `arrive`.

The vehicles transport totes along the aisle (one vehicle per tier). The time taken by the vehicle to process an order depends on the tote's location. The vehicle has to travel to this location, load the tote (it takes a fixed amount of time equal to `lv` seconds), then go back to the end of the aisle and, finally, unload the tote to the buffer (again this takes `lv` seconds). The speed profile of each vehicle is described as follows. First, the vehicle goes with a constant acceleration `av` *m/s$^2$* until it reaches its maximum velocity `vmaxv`, then it moves with this velocity and decelerates with a constant deceleration `av` to approach its destination point. If the tote is located too close to the end of the aisle, it is possible that the vehicle will not reach its maximum speed.

The vehicles unload the totes to a location where it is picked up by the lift. At any given time only one tote per tier is allowed to occupy such a position.

The lift transports the totes from every tier to the ground floor. The processing time depends on the tote's location and the fixed time to load and unload the tote (`ll` seconds for loading and `ll` seconds for unloading). The maximum speed of the lift is `vmaxl` *m/s* with a speed profile similar to that of the vehicles (constant acceleration/deceleration of `al` *m/s<sup>2</sup>*).

# 4 Modeling of the AVS/RS
The model consists of several processes communicating via channels, see Figure 3.

| Figure 3: The processes in the model | 
- 
<img src="figures/avrs.png" alt="drawing" width="400"/> 

A brief description of the processes is given below:
- **G:** The generator models the arrival of orders for totes. There is one generator per tier.
- **DB:** The demand buffer stores the orders to be picked up by the vehicles. The vehicle processes the orders under first-come-first-serve policy. It can always receive a tote, but it releases a tote only when the vehicle is ready to pick it up.
- **V:** The vehicle can be modeled as a server with a variable processing time.
- **GDV:** The process consisting of a Generator, Demand Buffer and Vehicle for one tier of the AVS/RS system.
- **B:** The buffer stores the totes from the vehicles awaiting for a pick-up by the lift. The buffer operates under first-come-first-serve policy and has a finite capacity of `bc` totes per tier. So, every tier has a buffer location of finite capacity of `bc` totes. All those locations together form the buffer B that accommodates all the totes which are processed by the same lift. When the buffer is not empty (there is at least one tote on one of the tiers), the buffer sends information about the tier of the longest waiting tote to the lift upon request. This information is used by the lift to determine the location of the tote (the number of the tier the tote is located in). Once the lift is ready to pick it up, the tote is released to the lift. There are two types of queues in the buffer: `xs` contains all the totes to be picked up by the lift and there are Level counters `n` counting the totes from the corresponding tier.
- **L:** The lift, similar to the process V, is modeled as a machine with a variable processing time. A lift first receives a destination tier. Then the process delays for time required for the lift to go to the tote location and pick up the tote. Then it receives the tote, and next it delays for the time required to go to the ground floor and to unload the tote. After that the lift process is ready to release the tote to the Exit process.
- **E:** In the exit process all the data related to each tote are collected. This process calculates the average throughput and the average flow-time. The number of totes to be processed by the AVS/RS during one simulation run is determined by the constant `Number_of_orders`.

# 5 Remark concerning report
All questions must be answered in this file (with the exeception of the lot-time diagrams, which must be attached as seperate files). Avoid unnecessary long explanations, however answers to analytical questions without an argument will result in no points. You can add extra Cells to add code or text (markdown) to the notebook. Markdown (text) boxes support Latex for writing formulas, e.g. `$ y = a \cdot x^2 $` turns into $ y = a \cdot x^2 $. More info: [Markdown](https://personal.math.ubc.ca/~pwalls/math-python/jupyter/markdown/) and [Latex](https://personal.math.ubc.ca/~pwalls/math-python/jupyter/latex/).

Both the notebook, and a PDF of the notebook must be submitted. To download the notebook file: click `File` > `Download as` > `Notebook (.ipynb)`. To download a PDF: press `Control + P` and `Save as PDF` (do not use the Jupyter Print options, as they will print the entire output of your simulations).

# 6 Assignment
When making a SimPy specification, one does not build an entire model and then starts debugging. A model is build step by step. During each step proper functionality is checked. We therefore model one process at a time, and connect the process with a Generator and/or Exit process to test proper functionality. In order to test proper functionality we first use analytical methods to determine the expected outcome. Then we run simulations to verify if these outcomes are indeed obtained. If that is the case, we can be more convinced that the process has been modeled correctly.


## 6.1 Exercise 1: Generator (5 points)
So the first step is to write a proper generator for a tier. To that end, the first model we build consists of (only) a Generator process and an Exit process collecting the totes generated by the Generator. The inter arrival time of requests is exponentially distributed with mean `arrive`. The requested tote should be retrieved from a random (uniformly distributed) column, where there are `depth` columns in total.

a. Determine (analytically) the throughput and flow time that should result from your model with only the generator process and the exit process.

Answer: 

The throughput is equal to the rate of arrival which is the inverse of the mean arrival time $r_a = 1/t_a = $ `1/arrive`\
Flow time is equal to zero as soon as the tote is created it goes to the exit

$\delta = 0$ \
$r_a = 1/t_a = \frac{1}{70} = 0.014$ 

b. Complete the simulation code from the following template:

In [121]:
# =================================
# Global
# =================================
arrive = 70.0             # inter arrival time of requests
depth  = 55               # the number of columns
number_of_orders = 10000  # the number of orders to process

meantroughput = float()
meanflowtime = float()

# =================================
# Tote
# =================================
@dataclass
class Tote:
    entrytime: float = 0.0
    column: int = 0

# =================================
# Generator
# =================================
@process
def Generator(env, c_out):
    x = Tote()
    while True:
        x.entrytime = env.now
        x.column = random.randint(0, depth) 
        yield env.execute(c_out.send(x))
        delay = random.exponential(arrive)
        yield env.timeout(delay)


# =================================
# Exit
# =================================


@process
def Exit(env, c_in, verbose: bool = True):
    global meantroughput, meanflowtime
    mphi = 0
    
    mincolumn = inf #using infinity as starting value
    maxcolumn = -inf #using negative infinity as starting value
    for i in range(1, number_of_orders + 1):
        x = yield env.execute(c_in.receive())
        mphi = (i - 1) / i * mphi + (env.now - x.entrytime) / i
        if verbose:
            print(f"tote = {i:6d};"  
                  f"  Entrytime = {x.entrytime: 10.4f};" 
                  f"  Column = {x.column:2d};"
                  f"  Mean throughput =" + (f"{i / env.now:8.6f}"   if   env.now   else f"{'N.A.':>8s}") +
                  f"  Mean flowtime = {mphi:6.4f}" 
            )
        #code to check the min an max column values
        if x.column > maxcolumn: 
            maxcolumn = x.column
        elif x.column < mincolumn:
            mincolumn = x.column
    meantroughput = i / env.now #setting global variables equal to the mean troughput and flow time
    meanflowtime = mphi
    if verbose:
        print(f"  Mincolumn = {mincolumn}, Maxcolumn = {maxcolumn}") #printing out the mincolum and max column
        print(
            f"  Mean throughput = " + (f"{i / env.now:8.6f}"   if   env.now   else f"{'N.A.':>8s}") +
            f"  Mean flowtime = {mphi:6.4f}" 
            ) #only print out the final mean throughput and flow time

# =================================
# Model
# =================================
def model(verbose : bool = True):
    env = Environment()
    a = Channel(env)
    G = Generator(env, a)
    E = Exit(env, a, verbose)
    env.run(until=E)
    if verbose:
        print ("simulatrion has ended")

# =================================
# Main
# =================================
model()

tote =      1;  Entrytime =     0.0000;  Column =  3;  Mean throughput =    N.A.  Mean flowtime = 0.0000
tote =      2;  Entrytime =   170.9459;  Column = 20;  Mean throughput =0.011700  Mean flowtime = 0.0000
tote =      3;  Entrytime =   221.3260;  Column = 17;  Mean throughput =0.013555  Mean flowtime = 0.0000
tote =      4;  Entrytime =   355.3924;  Column = 41;  Mean throughput =0.011255  Mean flowtime = 0.0000
tote =      5;  Entrytime =   368.3214;  Column = 34;  Mean throughput =0.013575  Mean flowtime = 0.0000
tote =      6;  Entrytime =   546.0579;  Column = 33;  Mean throughput =0.010988  Mean flowtime = 0.0000
tote =      7;  Entrytime =   607.0842;  Column = 36;  Mean throughput =0.011531  Mean flowtime = 0.0000
tote =      8;  Entrytime =   622.7061;  Column = 24;  Mean throughput =0.012847  Mean flowtime = 0.0000
tote =      9;  Entrytime =   909.5410;  Column = 19;  Mean throughput =0.009895  Mean flowtime = 0.0000
tote =     10;  Entrytime =  1083.1552;  Column = 16;  

tote =   1951;  Entrytime =  138141.5392;  Column = 42;  Mean throughput =0.014123  Mean flowtime = 0.0000
tote =   1952;  Entrytime =  138149.6038;  Column = 53;  Mean throughput =0.014130  Mean flowtime = 0.0000
tote =   1953;  Entrytime =  138215.8885;  Column = 39;  Mean throughput =0.014130  Mean flowtime = 0.0000
tote =   1954;  Entrytime =  138330.8034;  Column = 47;  Mean throughput =0.014126  Mean flowtime = 0.0000
tote =   1955;  Entrytime =  138363.1697;  Column = 21;  Mean throughput =0.014129  Mean flowtime = 0.0000
tote =   1956;  Entrytime =  138424.1098;  Column = 27;  Mean throughput =0.014130  Mean flowtime = 0.0000
tote =   1957;  Entrytime =  138491.6024;  Column = 40;  Mean throughput =0.014131  Mean flowtime = 0.0000
tote =   1958;  Entrytime =  138717.1811;  Column = 45;  Mean throughput =0.014115  Mean flowtime = 0.0000
tote =   1959;  Entrytime =  138744.6207;  Column =  6;  Mean throughput =0.014119  Mean flowtime = 0.0000
tote =   1960;  Entrytime =  138867.9

tote =   3880;  Entrytime =  274267.0435;  Column = 17;  Mean throughput =0.014147  Mean flowtime = 0.0000
tote =   3881;  Entrytime =  274364.9136;  Column =  7;  Mean throughput =0.014145  Mean flowtime = 0.0000
tote =   3882;  Entrytime =  274416.5820;  Column = 38;  Mean throughput =0.014146  Mean flowtime = 0.0000
tote =   3883;  Entrytime =  274495.3337;  Column = 49;  Mean throughput =0.014146  Mean flowtime = 0.0000
tote =   3884;  Entrytime =  274502.2488;  Column = 47;  Mean throughput =0.014149  Mean flowtime = 0.0000
tote =   3885;  Entrytime =  274554.1795;  Column = 20;  Mean throughput =0.014150  Mean flowtime = 0.0000
tote =   3886;  Entrytime =  274588.1256;  Column =  5;  Mean throughput =0.014152  Mean flowtime = 0.0000
tote =   3887;  Entrytime =  274589.0960;  Column =  2;  Mean throughput =0.014156  Mean flowtime = 0.0000
tote =   3888;  Entrytime =  274654.8956;  Column = 50;  Mean throughput =0.014156  Mean flowtime = 0.0000
tote =   3889;  Entrytime =  274664.7

tote =   5561;  Entrytime =  389069.5781;  Column =  9;  Mean throughput =0.014293  Mean flowtime = 0.0000
tote =   5562;  Entrytime =  389086.0276;  Column =  8;  Mean throughput =0.014295  Mean flowtime = 0.0000
tote =   5563;  Entrytime =  389176.2770;  Column =  6;  Mean throughput =0.014294  Mean flowtime = 0.0000
tote =   5564;  Entrytime =  389249.1864;  Column = 53;  Mean throughput =0.014294  Mean flowtime = 0.0000
tote =   5565;  Entrytime =  389317.3504;  Column = 15;  Mean throughput =0.014294  Mean flowtime = 0.0000
tote =   5566;  Entrytime =  389318.0947;  Column =  9;  Mean throughput =0.014297  Mean flowtime = 0.0000
tote =   5567;  Entrytime =  389357.7737;  Column = 53;  Mean throughput =0.014298  Mean flowtime = 0.0000
tote =   5568;  Entrytime =  389378.2542;  Column = 30;  Mean throughput =0.014300  Mean flowtime = 0.0000
tote =   5569;  Entrytime =  389540.1012;  Column = 32;  Mean throughput =0.014296  Mean flowtime = 0.0000
tote =   5570;  Entrytime =  389575.2

tote =   7387;  Entrytime =  515372.4249;  Column = 53;  Mean throughput =0.014333  Mean flowtime = 0.0000
tote =   7388;  Entrytime =  515376.6082;  Column = 28;  Mean throughput =0.014335  Mean flowtime = 0.0000
tote =   7389;  Entrytime =  515504.8766;  Column = 17;  Mean throughput =0.014334  Mean flowtime = 0.0000
tote =   7390;  Entrytime =  515513.3891;  Column = 51;  Mean throughput =0.014335  Mean flowtime = 0.0000
tote =   7391;  Entrytime =  515702.5434;  Column = 37;  Mean throughput =0.014332  Mean flowtime = 0.0000
tote =   7392;  Entrytime =  515744.0896;  Column = 14;  Mean throughput =0.014333  Mean flowtime = 0.0000
tote =   7393;  Entrytime =  515786.2821;  Column = 24;  Mean throughput =0.014333  Mean flowtime = 0.0000
tote =   7394;  Entrytime =  515801.4708;  Column = 14;  Mean throughput =0.014335  Mean flowtime = 0.0000
tote =   7395;  Entrytime =  515926.6904;  Column = 47;  Mean throughput =0.014333  Mean flowtime = 0.0000
tote =   7396;  Entrytime =  515982.0

tote =   9387;  Entrytime =  659067.6857;  Column = 37;  Mean throughput =0.014243  Mean flowtime = 0.0000
tote =   9388;  Entrytime =  659102.4109;  Column = 17;  Mean throughput =0.014244  Mean flowtime = 0.0000
tote =   9389;  Entrytime =  659106.2901;  Column = 23;  Mean throughput =0.014245  Mean flowtime = 0.0000
tote =   9390;  Entrytime =  659164.4102;  Column = 28;  Mean throughput =0.014245  Mean flowtime = 0.0000
tote =   9391;  Entrytime =  659235.5638;  Column = 39;  Mean throughput =0.014245  Mean flowtime = 0.0000
tote =   9392;  Entrytime =  659277.7907;  Column =  7;  Mean throughput =0.014246  Mean flowtime = 0.0000
tote =   9393;  Entrytime =  659289.3141;  Column = 38;  Mean throughput =0.014247  Mean flowtime = 0.0000
tote =   9394;  Entrytime =  659339.7276;  Column = 11;  Mean throughput =0.014248  Mean flowtime = 0.0000
tote =   9395;  Entrytime =  659352.5504;  Column = 28;  Mean throughput =0.014249  Mean flowtime = 0.0000
tote =   9396;  Entrytime =  659367.4

c. Confirm that your simulations produce the correct throughput and flow time. Also determine the minimal and maximal column returned by your simulation.

The mean throughput and mean flowtimes of the simulation are the smame as in the analytical solution.

As can be seen from the extra code added the minimum and maximum values of the column is 1 and 55 respectively. Which assuming that every column occurs in between is 55 spots.


In [63]:
1/70 

0.014285714285714285

Answer: ...




Run your simulation at least 10 times. What is the range of outcomes for the mean throughput? Determine (roughly, by trial and error) the number of orders required to get good estimates for the throughput (first three non-zero digits are correct).

Using the code bellow the simulation is done multiple times and statistics are collected, from this it can be concluded that in about 10 runs you usually have 3 digits of accuracy within the 95% confidence interval

In [64]:

def troughputanalysis(n):
    troughputes = list()
    flowtimes = list()
    for i in range(n):
        #doing multiple runs of the model
        model(False)
        troughputes.append(meantroughput)
        flowtimes.append(meanflowtime)
    
    stdev_th = statistics.stdev(troughputes)
    stdev_ph = statistics.stdev(flowtimes)

    print(f'Min mean troughput = {min(troughputes):8.6f}, Max mean troughput = {max(troughputes):8.6f}')
    print(f'Standard deviation mean troughput = {stdev_th:8.6f}')
    print(f'95% confidence interval mean troughput {statistics.mean(troughputes):8.6f} +/- {1.96 * stdev_th / sqrt(n):8.6f}')
    print(' ')
    print(f'Min mean flowtime = {min(flowtimes):8.6f}, Max mean flowtime = {max(flowtimes):8.6f}')
    print(f'Standard deviation mean flowtime = {stdev_ph:8.6f}')
    print(f'95% confidence interval mean flowtime {statistics.mean(flowtimes):8.6f} +/- {1.96 * stdev_ph / sqrt(n):8.6f}')

In [65]:
troughputanalysis(10)

Min mean troughput = 0.014061, Max mean troughput = 0.014480
Standard deviation mean troughput = 0.000136
95% confidence interval mean troughput 0.014287 +/- 0.000084
 
Min mean flowtime = 0.000000, Max mean flowtime = 0.000000
Standard deviation mean flowtime = 0.000000
95% confidence interval mean flowtime 0.000000 +/- 0.000000


## 6.2 Exercise 2: Demand Buffer (5 points)
Next, we include the Demand buffer which is modelled as a standard FIFO buffer with infinite capacity.

a. Determine (analytically) the throughput and flow time that should result from your model with only the generator process, demand buffer, and the exit process.

Answer: 
There is no bottleneck between the input and output of the buffer. This results in the fact that as soon as a tote is generated it's imediatly placed in the buffer and then also imediatly pushed in to the exit, resulting in a flow time of 0 seconds.

Again as there is no bottleneck in the buffer thus the throughput is also uneffected and still equal to rate at which totes are generated: $\delta = \frac{1}{70}$. However in reality it takes some computation time and therefore a slight decrease in troughput will be noticed when compared to the model without a buffer.

b. Complete the simulation code in the template below.

Note: The previously defined variables and functions remain unchanged, only the Demand Buffer is added, and the main code is changed.

In [66]:
# =================================
# Demand Buffer
# =================================
@process
def Demand_Buffer(env, c_in, c_out):
    xs = [] # list of totes
    while True:
        sending = c_out.send(xs[0]) if len(xs)>0 else None
        receiving = c_in.receive()
        x = yield env.select(sending, receiving)
        if selected(receiving):
            xs = xs + [x]
        if selected(sending):
            xs = xs[1:]
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = Channel(env)
    b = Channel(env)
    G = Generator(env, a)
    D = Demand_Buffer(env, a, b)
    E = Exit(env, b)
    env.run(until=E)
    print ("simulation has ended")
    
# =================================
# Main
# =================================
model()

tote =      1;  Entrytime =     0.0000;  Column = 21;  Mean throughput =    N.A.  Mean flowtime = 0.0000
tote =      2;  Entrytime =    77.6852;  Column = 17;  Mean throughput =0.025745  Mean flowtime = 0.0000
tote =      3;  Entrytime =    80.9821;  Column =  2;  Mean throughput =0.037045  Mean flowtime = 0.0000
tote =      4;  Entrytime =    83.4475;  Column = 34;  Mean throughput =0.047934  Mean flowtime = 0.0000
tote =      5;  Entrytime =   115.5830;  Column = 14;  Mean throughput =0.043259  Mean flowtime = 0.0000
tote =      6;  Entrytime =   160.7896;  Column = 24;  Mean throughput =0.037316  Mean flowtime = 0.0000
tote =      7;  Entrytime =   163.9193;  Column = 26;  Mean throughput =0.042704  Mean flowtime = 0.0000
tote =      8;  Entrytime =   425.1658;  Column = 39;  Mean throughput =0.018816  Mean flowtime = 0.0000
tote =      9;  Entrytime =   602.0212;  Column = 28;  Mean throughput =0.014950  Mean flowtime = 0.0000
tote =     10;  Entrytime =   656.7956;  Column = 41;  

tote =   1084;  Entrytime =  74910.8393;  Column = 52;  Mean throughput =0.014471  Mean flowtime = 0.0000
tote =   1085;  Entrytime =  74972.3746;  Column = 10;  Mean throughput =0.014472  Mean flowtime = 0.0000
tote =   1086;  Entrytime =  75154.3485;  Column = 31;  Mean throughput =0.014450  Mean flowtime = 0.0000
tote =   1087;  Entrytime =  75462.0238;  Column =  6;  Mean throughput =0.014405  Mean flowtime = 0.0000
tote =   1088;  Entrytime =  75480.9614;  Column = 26;  Mean throughput =0.014414  Mean flowtime = 0.0000
tote =   1089;  Entrytime =  75488.1679;  Column = 18;  Mean throughput =0.014426  Mean flowtime = 0.0000
tote =   1090;  Entrytime =  75507.7147;  Column =  5;  Mean throughput =0.014436  Mean flowtime = 0.0000
tote =   1091;  Entrytime =  75569.2691;  Column = 37;  Mean throughput =0.014437  Mean flowtime = 0.0000
tote =   1092;  Entrytime =  75575.7811;  Column = 41;  Mean throughput =0.014449  Mean flowtime = 0.0000
tote =   1093;  Entrytime =  75597.1145;  Colu

tote =   1176;  Entrytime =  81827.7570;  Column = 18;  Mean throughput =0.014372  Mean flowtime = 0.0000
tote =   1177;  Entrytime =  81973.0252;  Column = 20;  Mean throughput =0.014358  Mean flowtime = 0.0000
tote =   1178;  Entrytime =  82040.6048;  Column = 13;  Mean throughput =0.014359  Mean flowtime = 0.0000
tote =   1179;  Entrytime =  82105.8423;  Column = 38;  Mean throughput =0.014360  Mean flowtime = 0.0000
tote =   1180;  Entrytime =  82127.8040;  Column = 46;  Mean throughput =0.014368  Mean flowtime = 0.0000
tote =   1181;  Entrytime =  82193.6622;  Column = 11;  Mean throughput =0.014369  Mean flowtime = 0.0000
tote =   1182;  Entrytime =  82311.2204;  Column = 54;  Mean throughput =0.014360  Mean flowtime = 0.0000
tote =   1183;  Entrytime =  82373.1156;  Column = 35;  Mean throughput =0.014361  Mean flowtime = 0.0000
tote =   1184;  Entrytime =  82391.5255;  Column = 29;  Mean throughput =0.014370  Mean flowtime = 0.0000
tote =   1185;  Entrytime =  82402.2306;  Colu

tote =   2118;  Entrytime =  146041.8699;  Column = 46;  Mean throughput =0.014503  Mean flowtime = 0.0000
tote =   2119;  Entrytime =  146074.6015;  Column = 29;  Mean throughput =0.014506  Mean flowtime = 0.0000
tote =   2120;  Entrytime =  146076.4986;  Column = 53;  Mean throughput =0.014513  Mean flowtime = 0.0000
tote =   2121;  Entrytime =  146131.3821;  Column =  6;  Mean throughput =0.014514  Mean flowtime = 0.0000
tote =   2122;  Entrytime =  146383.4621;  Column = 18;  Mean throughput =0.014496  Mean flowtime = 0.0000
tote =   2123;  Entrytime =  146396.0549;  Column = 22;  Mean throughput =0.014502  Mean flowtime = 0.0000
tote =   2124;  Entrytime =  146438.4888;  Column = 33;  Mean throughput =0.014504  Mean flowtime = 0.0000
tote =   2125;  Entrytime =  146467.3232;  Column =  2;  Mean throughput =0.014508  Mean flowtime = 0.0000
tote =   2126;  Entrytime =  146525.9916;  Column = 52;  Mean throughput =0.014509  Mean flowtime = 0.0000
tote =   2127;  Entrytime =  146603.5

tote =   2252;  Entrytime =  154975.2772;  Column = 36;  Mean throughput =0.014531  Mean flowtime = 0.0000
tote =   2253;  Entrytime =  155063.5782;  Column = 11;  Mean throughput =0.014530  Mean flowtime = 0.0000
tote =   2254;  Entrytime =  155341.0344;  Column = 21;  Mean throughput =0.014510  Mean flowtime = 0.0000
tote =   2255;  Entrytime =  155411.4447;  Column = 26;  Mean throughput =0.014510  Mean flowtime = 0.0000
tote =   2256;  Entrytime =  155552.1892;  Column = 25;  Mean throughput =0.014503  Mean flowtime = 0.0000
tote =   2257;  Entrytime =  155573.4903;  Column = 52;  Mean throughput =0.014508  Mean flowtime = 0.0000
tote =   2258;  Entrytime =  155604.4455;  Column =  1;  Mean throughput =0.014511  Mean flowtime = 0.0000
tote =   2259;  Entrytime =  156062.1178;  Column = 31;  Mean throughput =0.014475  Mean flowtime = 0.0000
tote =   2260;  Entrytime =  156088.5852;  Column =  3;  Mean throughput =0.014479  Mean flowtime = 0.0000
tote =   2261;  Entrytime =  156101.9

...

tote =   7413;  Entrytime =  522879.4175;  Column = 41;  Mean throughput =0.014177  Mean flowtime = 0.0000
tote =   7414;  Entrytime =  522972.7343;  Column = 15;  Mean throughput =0.014177  Mean flowtime = 0.0000
tote =   7415;  Entrytime =  523007.3330;  Column = 41;  Mean throughput =0.014178  Mean flowtime = 0.0000
tote =   7416;  Entrytime =  523063.8979;  Column = 46;  Mean throughput =0.014178  Mean flowtime = 0.0000
tote =   7417;  Entrytime =  523077.7343;  Column =  4;  Mean throughput =0.014180  Mean flowtime = 0.0000
tote =   7418;  Entrytime =  523156.9000;  Column = 14;  Mean throughput =0.014179  Mean flowtime = 0.0000
tote =   7419;  Entrytime =  523242.2821;  Column =  3;  Mean throughput =0.014179  Mean flowtime = 0.0000
tote =   7420;  Entrytime =  523277.8397;  Column = 35;  Mean throughput =0.014180  Mean flowtime = 0.0000
tote =   7421;  Entrytime =  523551.9118;  Column = 32;  Mean throughput =0.014174  Mean flowtime = 0.0000
tote =   7422;  Entrytime =  523557.6

tote =   8057;  Entrytime =  568873.3055;  Column = 23;  Mean throughput =0.014163  Mean flowtime = 0.0000
tote =   8058;  Entrytime =  568965.4850;  Column =  2;  Mean throughput =0.014163  Mean flowtime = 0.0000
tote =   8059;  Entrytime =  568969.3462;  Column = 50;  Mean throughput =0.014164  Mean flowtime = 0.0000
tote =   8060;  Entrytime =  569102.5587;  Column = 15;  Mean throughput =0.014163  Mean flowtime = 0.0000
tote =   8061;  Entrytime =  569145.1861;  Column =  6;  Mean throughput =0.014163  Mean flowtime = 0.0000
tote =   8062;  Entrytime =  569185.3584;  Column = 33;  Mean throughput =0.014164  Mean flowtime = 0.0000
tote =   8063;  Entrytime =  569374.4511;  Column = 51;  Mean throughput =0.014161  Mean flowtime = 0.0000
tote =   8064;  Entrytime =  569431.1068;  Column =  3;  Mean throughput =0.014162  Mean flowtime = 0.0000
tote =   8065;  Entrytime =  569596.9844;  Column =  5;  Mean throughput =0.014159  Mean flowtime = 0.0000
tote =   8066;  Entrytime =  569601.4

tote =   8464;  Entrytime =  596855.1586;  Column = 15;  Mean throughput =0.014181  Mean flowtime = 0.0000
tote =   8465;  Entrytime =  596866.1760;  Column = 28;  Mean throughput =0.014182  Mean flowtime = 0.0000
tote =   8466;  Entrytime =  596890.5183;  Column = 16;  Mean throughput =0.014184  Mean flowtime = 0.0000
tote =   8467;  Entrytime =  596896.1500;  Column = 16;  Mean throughput =0.014185  Mean flowtime = 0.0000
tote =   8468;  Entrytime =  597003.8701;  Column = 43;  Mean throughput =0.014184  Mean flowtime = 0.0000
tote =   8469;  Entrytime =  597053.3910;  Column = 46;  Mean throughput =0.014185  Mean flowtime = 0.0000
tote =   8470;  Entrytime =  597080.3802;  Column = 38;  Mean throughput =0.014186  Mean flowtime = 0.0000
tote =   8471;  Entrytime =  597091.4567;  Column = 11;  Mean throughput =0.014187  Mean flowtime = 0.0000
tote =   8472;  Entrytime =  597181.6853;  Column = 24;  Mean throughput =0.014187  Mean flowtime = 0.0000
tote =   8473;  Entrytime =  597241.1

tote =   9246;  Entrytime =  653723.2870;  Column = 42;  Mean throughput =0.014144  Mean flowtime = 0.0000
tote =   9247;  Entrytime =  653752.7410;  Column = 10;  Mean throughput =0.014144  Mean flowtime = 0.0000
tote =   9248;  Entrytime =  653813.2698;  Column = 15;  Mean throughput =0.014145  Mean flowtime = 0.0000
tote =   9249;  Entrytime =  653845.3539;  Column = 25;  Mean throughput =0.014146  Mean flowtime = 0.0000
tote =   9250;  Entrytime =  654009.0450;  Column = 43;  Mean throughput =0.014144  Mean flowtime = 0.0000
tote =   9251;  Entrytime =  654242.8854;  Column = 44;  Mean throughput =0.014140  Mean flowtime = 0.0000
tote =   9252;  Entrytime =  654313.6355;  Column = 33;  Mean throughput =0.014140  Mean flowtime = 0.0000
tote =   9253;  Entrytime =  654424.0897;  Column =  7;  Mean throughput =0.014139  Mean flowtime = 0.0000
tote =   9254;  Entrytime =  654427.0270;  Column = 36;  Mean throughput =0.014141  Mean flowtime = 0.0000
tote =   9255;  Entrytime =  654427.9

tote =   9515;  Entrytime =  671666.9936;  Column = 30;  Mean throughput =0.014166  Mean flowtime = 0.0000
tote =   9516;  Entrytime =  671719.3501;  Column = 24;  Mean throughput =0.014167  Mean flowtime = 0.0000
tote =   9517;  Entrytime =  671751.4933;  Column = 52;  Mean throughput =0.014167  Mean flowtime = 0.0000
tote =   9518;  Entrytime =  671851.2382;  Column =  4;  Mean throughput =0.014167  Mean flowtime = 0.0000
tote =   9519;  Entrytime =  671859.1810;  Column = 32;  Mean throughput =0.014168  Mean flowtime = 0.0000
tote =   9520;  Entrytime =  672066.8847;  Column = 34;  Mean throughput =0.014165  Mean flowtime = 0.0000
tote =   9521;  Entrytime =  672068.8720;  Column =  7;  Mean throughput =0.014167  Mean flowtime = 0.0000
tote =   9522;  Entrytime =  672075.2263;  Column = 49;  Mean throughput =0.014168  Mean flowtime = 0.0000
tote =   9523;  Entrytime =  672091.7062;  Column = 14;  Mean throughput =0.014169  Mean flowtime = 0.0000
tote =   9524;  Entrytime =  672140.8

c. Confirm that your simulations produce the correct throughput and flow time.

Answer: The mean troughut and mean flowtime have not changed, which is what was predicted from the analytical solution



## 6.3 Exercise 3: Vehicle as machine (5 points)
Next, we include the Vehicle which as a first attempt is modelled as a standard machine with a deterministic processing time of 40.0 seconds

a. Determine (analytically) the throughput and flow time that should result from your model with only the generator process, demand buffer, vehicle and the exit process.

Answer: 
- First calculate the utilization, with $ t_0 = 40 $ and $ t_a = 70 $: 

$ u = \frac{t_0}{t_a} = 0.5714 $

- then the flow can be calculated with the following formula: 

$ \varphi = \gamma \cdot \frac{u}{1-u} \cdot t_0 + t_0 = 66.67 $

- The throughput of the system is still the same as the processing time of the vehicle is lower than 70:

$ Throughput = \frac{1}{arrive} = \frac{1}{70} = 0.0143 $


b. Complete the simulation code in the template below.

Note: The previously defined variables and functions remain unchanged, only the Vehicle is added, and the main code is changed.

In [67]:
# =================================
# Vehicle
# =================================
te_Vehicle = 40 #seconds

@process
def Vehicle(env, c_in, c_out):
    while True:
        receiving = c_in.receive() 
        yield env.execute(receiving) #waiting until something is received
        yield env.timeout(te_Vehicle) #waiting for the process time
        sending = c_out.send(receiving.entity) #sending out the received entity 
        yield env.execute(sending) 
    #.....
        
# =================================
# Model
# =================================
def model(verbose : bool = True):
    env = Environment()
    a = Channel(env)
    b = Channel(env)
    c = Channel(env)
    G = Generator(env, a)
    D = Demand_Buffer(env, a, b)
    V = Vehicle(env, b, c)
    E = Exit(env, c, verbose)
    env.run(until=E)
    print ("simulation has ended")

# =================================
# Main
# =================================
model()

tote =      1;  Entrytime =    10.0926;  Column = 24;  Mean throughput =0.025000  Mean flowtime = 29.9074
tote =      2;  Entrytime =    63.1651;  Column = 20;  Mean throughput =0.025000  Mean flowtime = 23.3712
tote =      3;  Entrytime =   116.1193;  Column = 16;  Mean throughput =0.025000  Mean flowtime = 16.8743
tote =      4;  Entrytime =   116.1193;  Column = 16;  Mean throughput =0.025000  Mean flowtime = 23.6259
tote =      5;  Entrytime =   197.8405;  Column = 30;  Mean throughput =0.022918  Mean flowtime = 22.9673
tote =      6;  Entrytime =   197.8405;  Column = 30;  Mean throughput =0.023240  Mean flowtime = 29.1948
tote =      7;  Entrytime =   293.5184;  Column = 22;  Mean throughput =0.023476  Mean flowtime = 25.6891
tote =      8;  Entrytime =   325.4371;  Column = 48;  Mean throughput =0.023657  Mean flowtime = 24.0700
tote =      9;  Entrytime =   346.3511;  Column = 33;  Mean throughput =0.023799  Mean flowtime = 24.9313
tote =     10;  Entrytime =   346.3511;  Colum

tote =    127;  Entrytime =  8242.5208;  Column =  7;  Mean throughput =0.015362  Mean flowtime = 38.6595
tote =    128;  Entrytime =  8242.5208;  Column =  7;  Mean throughput =0.015408  Mean flowtime = 38.8637
tote =    129;  Entrytime =  8242.5208;  Column =  7;  Mean throughput =0.015454  Mean flowtime = 39.3749
tote =    130;  Entrytime =  8242.5208;  Column =  7;  Mean throughput =0.015500  Mean flowtime = 40.1859
tote =    131;  Entrytime =  8242.5208;  Column =  7;  Mean throughput =0.015545  Mean flowtime = 41.2898
tote =    132;  Entrytime =  8482.3608;  Column = 12;  Mean throughput =0.015546  Mean flowtime = 41.0400
tote =    133;  Entrytime =  8520.8983;  Column = 29;  Mean throughput =0.015591  Mean flowtime = 40.8049
tote =    134;  Entrytime =  8552.5318;  Column = 46;  Mean throughput =0.015635  Mean flowtime = 40.6358
tote =    135;  Entrytime =  8608.8531;  Column = 12;  Mean throughput =0.015678  Mean flowtime = 40.3483
tote =    136;  Entrytime =  8608.8531;  Colum

tote =    338;  Entrytime =  23816.4835;  Column = 45;  Mean throughput =0.014149  Mean flowtime = 39.7884
tote =    339;  Entrytime =  23906.4686;  Column = 29;  Mean throughput =0.014167  Mean flowtime = 39.7362
tote =    340;  Entrytime =  23906.4686;  Column = 29;  Mean throughput =0.014185  Mean flowtime = 39.8020
tote =    341;  Entrytime =  24049.2140;  Column = 49;  Mean throughput =0.014156  Mean flowtime = 39.8026
tote =    342;  Entrytime =  24134.2078;  Column = 27;  Mean throughput =0.014167  Mean flowtime = 39.7057
tote =    343;  Entrytime =  24154.8060;  Column = 30;  Mean throughput =0.014185  Mean flowtime = 39.6659
tote =    344;  Entrytime =  24183.0208;  Column = 38;  Mean throughput =0.014203  Mean flowtime = 39.6606
tote =    345;  Entrytime =  24183.0208;  Column = 38;  Mean throughput =0.014220  Mean flowtime = 39.7713
tote =    346;  Entrytime =  24329.4912;  Column = 37;  Mean throughput =0.014198  Mean flowtime = 39.7720
tote =    347;  Entrytime =  24415.13

tote =    805;  Entrytime =  59297.8527;  Column = 11;  Mean throughput =0.013566  Mean flowtime = 39.1689
tote =    806;  Entrytime =  59430.2939;  Column =  4;  Mean throughput =0.013554  Mean flowtime = 39.1658
tote =    807;  Entrytime =  59497.0339;  Column = 16;  Mean throughput =0.013561  Mean flowtime = 39.1296
tote =    808;  Entrytime =  59497.0339;  Column = 16;  Mean throughput =0.013569  Mean flowtime = 39.1429
tote =    809;  Entrytime =  59647.3776;  Column =  3;  Mean throughput =0.013554  Mean flowtime = 39.1440
tote =    810;  Entrytime =  59728.1421;  Column = 10;  Mean throughput =0.013561  Mean flowtime = 39.0987
tote =    811;  Entrytime =  59728.1421;  Column = 10;  Mean throughput =0.013569  Mean flowtime = 39.1029
tote =    812;  Entrytime =  59893.4280;  Column = 14;  Mean throughput =0.013551  Mean flowtime = 39.0900
tote =    813;  Entrytime =  59893.4280;  Column = 14;  Mean throughput =0.013559  Mean flowtime = 39.1262
tote =    814;  Entrytime =  59893.42

tote =    992;  Entrytime =  71050.3008;  Column =  8;  Mean throughput =0.013961  Mean flowtime = 39.1741
tote =    993;  Entrytime =  71054.8710;  Column = 18;  Mean throughput =0.013968  Mean flowtime = 39.1731
tote =    994;  Entrytime =  71106.5307;  Column = 10;  Mean throughput =0.013974  Mean flowtime = 39.1604
tote =    995;  Entrytime =  71106.5307;  Column = 10;  Mean throughput =0.013980  Mean flowtime = 39.1880
tote =    996;  Entrytime =  71106.5307;  Column = 10;  Mean throughput =0.013986  Mean flowtime = 39.2556
tote =    997;  Entrytime =  71252.3057;  Column = 19;  Mean throughput =0.013992  Mean flowtime = 39.2170
tote =    998;  Entrytime =  71253.5191;  Column = 49;  Mean throughput =0.013999  Mean flowtime = 39.2174
tote =    999;  Entrytime =  71317.8402;  Column = 44;  Mean throughput =0.014005  Mean flowtime = 39.1934
tote =   1000;  Entrytime =  71344.8240;  Column =  2;  Mean throughput =0.014011  Mean flowtime = 39.1824
tote =   1001;  Entrytime =  71344.82

...

tote =   8895;  Entrytime =  627884.2388;  Column = 48;  Mean throughput =0.014166  Mean flowtime = 39.9791
tote =   8896;  Entrytime =  627999.9969;  Column =  1;  Mean throughput =0.014165  Mean flowtime = 39.9762
tote =   8897;  Entrytime =  627999.9969;  Column =  1;  Mean throughput =0.014166  Mean flowtime = 39.9778
tote =   8898;  Entrytime =  628112.0384;  Column = 11;  Mean throughput =0.014165  Mean flowtime = 39.9778
tote =   8899;  Entrytime =  628163.5269;  Column = 50;  Mean throughput =0.014166  Mean flowtime = 39.9778
tote =   8900;  Entrytime =  628343.4231;  Column = 54;  Mean throughput =0.014163  Mean flowtime = 39.9778
tote =   8901;  Entrytime =  628385.1839;  Column = 28;  Mean throughput =0.014164  Mean flowtime = 39.9778
tote =   8902;  Entrytime =  628437.5598;  Column = 17;  Mean throughput =0.014165  Mean flowtime = 39.9769
tote =   8903;  Entrytime =  628437.5598;  Column = 17;  Mean throughput =0.014165  Mean flowtime = 39.9804
tote =   8904;  Entrytime = 

tote =   9111;  Entrytime =  641883.7708;  Column = 27;  Mean throughput =0.014193  Mean flowtime = 39.9609
tote =   9112;  Entrytime =  642009.9507;  Column = 29;  Mean throughput =0.014193  Mean flowtime = 39.9582
tote =   9113;  Entrytime =  642009.9507;  Column = 29;  Mean throughput =0.014193  Mean flowtime = 39.9598
tote =   9114;  Entrytime =  642162.8212;  Column = 55;  Mean throughput =0.014192  Mean flowtime = 39.9598
tote =   9115;  Entrytime =  642256.3856;  Column = 15;  Mean throughput =0.014191  Mean flowtime = 39.9598
tote =   9116;  Entrytime =  642410.0381;  Column = 43;  Mean throughput =0.014189  Mean flowtime = 39.9598
tote =   9117;  Entrytime =  642651.3523;  Column = 39;  Mean throughput =0.014186  Mean flowtime = 39.9590
tote =   9118;  Entrytime =  642697.1305;  Column = 20;  Mean throughput =0.014186  Mean flowtime = 39.9576
tote =   9119;  Entrytime =  642697.1305;  Column = 20;  Mean throughput =0.014187  Mean flowtime = 39.9605
tote =   9120;  Entrytime = 

tote =   9306;  Entrytime =  655418.3148;  Column = 36;  Mean throughput =0.014198  Mean flowtime = 39.9382
tote =   9307;  Entrytime =  655418.3148;  Column = 36;  Mean throughput =0.014199  Mean flowtime = 39.9412
tote =   9308;  Entrytime =  655547.6424;  Column = 45;  Mean throughput =0.014199  Mean flowtime = 39.9375
tote =   9309;  Entrytime =  655579.6998;  Column = 48;  Mean throughput =0.014199  Mean flowtime = 39.9347
tote =   9310;  Entrytime =  655579.6998;  Column = 48;  Mean throughput =0.014200  Mean flowtime = 39.9361
tote =   9311;  Entrytime =  655637.8636;  Column = 36;  Mean throughput =0.014201  Mean flowtime = 39.9356
tote =   9312;  Entrytime =  655637.8636;  Column = 36;  Mean throughput =0.014201  Mean flowtime = 39.9394
tote =   9313;  Entrytime =  655773.5414;  Column = 51;  Mean throughput =0.014201  Mean flowtime = 39.9394
tote =   9314;  Entrytime =  655856.2365;  Column = 51;  Mean throughput =0.014201  Mean flowtime = 39.9364
tote =   9315;  Entrytime = 

tote =   9720;  Entrytime =  685030.4648;  Column =  5;  Mean throughput =0.014189  Mean flowtime = 39.9617
tote =   9721;  Entrytime =  685030.4648;  Column =  5;  Mean throughput =0.014189  Mean flowtime = 39.9634
tote =   9722;  Entrytime =  685197.0192;  Column = 38;  Mean throughput =0.014188  Mean flowtime = 39.9634
tote =   9723;  Entrytime =  685276.0608;  Column = 54;  Mean throughput =0.014188  Mean flowtime = 39.9634
tote =   9724;  Entrytime =  685327.7484;  Column = 22;  Mean throughput =0.014188  Mean flowtime = 39.9634
tote =   9725;  Entrytime =  685380.6174;  Column = 48;  Mean throughput =0.014188  Mean flowtime = 39.9629
tote =   9726;  Entrytime =  685380.6174;  Column = 48;  Mean throughput =0.014189  Mean flowtime = 39.9665
tote =   9727;  Entrytime =  685558.9436;  Column = 55;  Mean throughput =0.014188  Mean flowtime = 39.9665
tote =   9728;  Entrytime =  685774.2954;  Column = 40;  Mean throughput =0.014185  Mean flowtime = 39.9646
tote =   9729;  Entrytime = 

tote =   9917;  Entrytime =  698154.0913;  Column = 24;  Mean throughput =0.014204  Mean flowtime = 39.9589
tote =   9918;  Entrytime =  698154.0913;  Column = 24;  Mean throughput =0.014205  Mean flowtime = 39.9606
tote =   9919;  Entrytime =  698221.1327;  Column = 48;  Mean throughput =0.014205  Mean flowtime = 39.9606
tote =   9920;  Entrytime =  698280.5678;  Column = 27;  Mean throughput =0.014206  Mean flowtime = 39.9606
tote =   9921;  Entrytime =  698424.0711;  Column = 36;  Mean throughput =0.014205  Mean flowtime = 39.9570
tote =   9922;  Entrytime =  698464.1987;  Column = 42;  Mean throughput =0.014205  Mean flowtime = 39.9534
tote =   9923;  Entrytime =  698464.1987;  Column = 42;  Mean throughput =0.014206  Mean flowtime = 39.9539
tote =   9924;  Entrytime =  698464.1987;  Column = 42;  Mean throughput =0.014207  Mean flowtime = 39.9583
tote =   9925;  Entrytime =  698622.0893;  Column = 32;  Mean throughput =0.014206  Mean flowtime = 39.9583
tote =   9926;  Entrytime = 

c. Confirm that your simulations produce the correct throughput and flow time.

Answer: 

Running the model with the proccesing time set equal to 40: `te_Vehicle = 40` results in the expected throughput and mean flow time as described before.

Running the model with the proccessing time set equal to a value higher than the mean interarival time result in a decrease of the mean throughput. If we set the proccesing time equal to for example 100 it results in an mean throughput of 0.01  which is as to be expected from the analytical solution.



d. Run your simulation at least 10 times. What is the range of outcomes for the mean throughput? Determine (roughly/ by trial and error) the number of orders required to get good estimates for the flow time (first three non-zero digits are correct).

Answer: ...

You need about 10 runs to to get to a 3 digit accuracy with the 95 percent confidence interval. However due to run to run variance you don't always get 3 digits accuracy.


In [68]:
troughputanalysis(10)

simulation has ended
simulation has ended
simulation has ended
simulation has ended
simulation has ended
simulation has ended
simulation has ended
simulation has ended
simulation has ended
simulation has ended
Min mean troughput = 0.014019, Max mean troughput = 0.014419
Standard deviation mean troughput = 0.000121
95% confidence interval mean troughput 0.014263 +/- 0.000075
 
Min mean flowtime = 39.621939, Max mean flowtime = 40.401899
Standard deviation mean flowtime = 0.243017
95% confidence interval mean flowtime 40.041597 +/- 0.150624


## 6.4 Exercise 4: Vehicle accurately modelled (15 points)
Assume that a vehicle starts from the buffer. If it has to go to column $i \in \{0, depth - 1\}$, it needs to drive a distance $dv \cdot (i + 1)$, pick up the tote, drive back, and deliver the tote to the buffer. For driving the required distance, the vehicle first goes with a constant acceleration `av` *m/s$^2$* until it reaches its maximum velocity `vmaxv`, then it moves with this velocity and decelerates with a constant deceleration `av` to approach its destination point. If the tote is located too close to the end of the aisle, it is possible that the vehicle will not reach its maximum speed. 

a. From this information, (analytically) determine the time (in seconds) it takes a vehicle to drive a given distance of x meters. To that end, first determine from the acceleration profile the travelled distance as function of time. From that you can determine the time required to travel a given distance.

Answer: 

The expression for this movement differs from whether the vehicle will reach its maximum speed. 

Lets firt work out what happens if the vehicle will not reach its max speed. The distance travelled at a constant speed is:

$ x = \frac{1}{2} av \cdot t\ ^2 $ 

Resulting in the time travelled being for a given distance with constant acceleration:

$t = \sqrt{\frac{2x}{av}} $

Because the vehicle has to come to a stop it spends the same amount of time / distance accelerating and as it spends decelerating
$ x_{decel} = x_{accel} $ 

 Which means that the time spend decelerating is for $x = \frac{1}{2} $ but it does this twice resulting the following travel time:
 
$t_a = 2\sqrt{\frac{d}{av}}$


The time needed to reach the max velocity is:

$t_{amaxv} = vmaxv /av $

Next we want to know the distance traveled with constant acceleration.

$d_{a} = 0.5 \cdot av \cdot t_{amaxv}^2 $

Then the distance traveled at vmax

$ d_{vmax} = d - 2 * d_{a} $

Then finnally we have the time traveled at vmax

$ t_{vmax} = d_{vmax} / vmaxv $

Then combinding the accleration and constant velocity time results in the total time

$ t = 2 \cdot t_{amaxv} + t_{vmaxv} $

b. Next, if loading and unloading a tote both take `lv` seconds, determine (analytically) the time it takes a vehicle, starting from the buffer, to pick up a tote from column $i \in \{0, depth\}$ and deliver it to the buffer.

Answer: 

To come to this answer the only thing that needs to happen is to fill in $ dv(i + 1) $ for x and add $ 2 \cdot lv $, for both loading and unloading. 

If the vehicle will not reach its max speed, then: 
$ t_{1} = 4\sqrt{\frac{dv(i + 1)}{av}} + 2lv $ 
- for $ dv(i + 1) \leq \frac{vmaxv\ ^2}{av} $

If the vehicle will reach its maximum speed then: 
$ t_{2} = 2 \cdot (\frac{2\cdot\ vmaxv}{av} + \frac{dv(i + 1)-\frac{vmaxv\ ^2}{av}}{vmaxv} + lv) $
- for $ dv(i + 1) > \frac{vmaxv\ ^2}{av} $

The boundaries can also be refined by filling in values and solving for i in: 
$ i = \frac{vmaxv\ ^2}{av \cdot dv} - 1 = \frac{1.5^2}{1\cdot0.5} - 1 = 3.5 $

As i is an integer, this means that the maximum speed is not reached for collumn 0,1,2,3 and will be reached for all others




c. Determine (analytically) the mean and variance of this total travel time for a random (uniformly distributed) column.

Answer: 

As the collumn selection is a uniform distribution, the chances for all instances of i are equal, meaning the time for every possible trip to collumn i needs to be added up and devided by the total amount of possible outcomes. As the load and unload times are always the same these can be kept out of the sum. Filling the depth of 55 and the other values as stated below: 

$ t_0 = 2 \cdot lv + \frac{1}{55} (\sum_{k=0}^{3} 4 \sqrt{\frac{dv(k+1)}{av}} + \sum_{j=4}^{54} 2 (\frac{vmaxv}{av}+\frac{dv(j+i)}{vmaxv}) = 27.64 [s] $

With the mean travel time the time varience can be calculated: 

$ var(t_0) = \frac{1}{55} (\sum_{k=0}^{3} (4 \sqrt{\frac{dv(k+1)}{av}} + 2lv -t_0)^2 + \sum_{j=4}^{54} 2 (\frac{vmaxv}{av}+\frac{dv(j+i)}{vmaxv} + 2lv -t_0)^2 = 112.84 [s^2] $


In [69]:
lv = 3.0                  # time to load/unload the vehicle
dv = 0.5                  # unit width clearance
vmaxv = 1.5              # maximum velocity of the vehicle
av = 1.0                  # acceleration/deceleration of the vehicle

t0 = 2*lv
for i in range(depth):
    if i <= 3:
        t0 = t0 + 1/depth * 4 * sqrt(dv*(i+1)/av)
    else:
        t0 = t0 + 1/depth * 2 * (vmaxv/av + dv*(i+1)/vmaxv)
print(f't0 = {t0:2.2f}')

vart0 = 0
for i in range(depth):
    if i <= 3:
        vart0 = vart0 + 1/depth * ( 4 * sqrt(dv*(i+1)/av) + 2*lv - t0)**2 
    else:
        vart0 = vart0 + 1/depth * (2*(vmaxv/av + dv*(i+1)/vmaxv) + 2*lv- t0)**2 
        
print(f'var(t0) = {vart0:2.2f}')

t0 = 27.64
var(t0) = 112.84


d. Determine (analytically) the throughput and flow time that should result from your model with only the generator process, demand buffer, vehicle and the exit process.

Answer:

- The throughput of the system is still the same as the mean travel time of the vehicle is lower than 70:

$ Throughput = \frac{1}{arrive} = \frac{1}{70} = 0.0143 $


e. Complete the simulation code in the template below, incorporating the actual time a vehicle requires for picking up a tote and delivering it to the buffer.

Note: the previously defined function processes remain unchanged, only the Vehicle needs to be redefined.

In [70]:
def traveltimevehicle(d, vmaxv, av):
    #Function to compute travel time
    t_amaxv = vmaxv / av  #acceleration/deceleration time
    x_amaxv = 0.5 * av * t_amaxv**2 #distance travel in acceleration/deceleration time

    if d >= 2 * x_amaxv: #Vehicle reaches vmax
        d_vmax = d - 2 * x_amaxv #distance traveled at vmax
        t_vmax = d_vmax / vmaxv #amount of time traveled at vmax
        t = (2 * t_amaxv + t_vmax); #total time traveling = traveling at vmax + acceleration & deceleration time
    else: #vehicle does not reach vmax
        t = 2*sqrt(d/av)
    
    return t


#validating the traveltimevehicle function
vmaxv = 1.5              # maximum velocity of the vehicle
av = 1.0                  # acceleration/deceleration of the vehicle

vmaxl = 5.0     # maximum velocity of lift
al = 7.0        # acceleration/deceleration of lift


t = list()
distance = list()
scale = 0.01
for i in range(round(55*0.5/scale)):
    d = scale * i  #distance to tote
    distance.append(d)
    t.append(traveltimevehicle(d, vmaxv, av))
    

fig = plt.figure()
ax = fig.add_subplot()
ax.plot(distance,t)
ax.set_xlabel("distance (unit)")
ax.set_ylabel("Time (s)")
ax.set_title("Distance versus travel time")

<IPython.core.display.Javascript object>

Text(0.5, 1.0, 'Distance versus travel time')

As can be seen in the test code above the travel time first increases with the square root of the distance and after it reaches the maximal velocity it the travel time increases linearly with the distance.

In [71]:
# =================================
# Global vehicle variables
# =================================
lv = 3.0                  # time to load/unload the vehicle
dv = 0.5                  # unit width clearance
vmaxv = 1.5              # maximum velocity of the vehicle
av = 1.0                  # acceleration/deceleration of the vehicle

t_amaxv = vmaxv / av  #acceleration/deceleration time
x_amaxv = 0.5 * av * t_amaxv**2 #distance travel in acceleration/deceleration time
# =================================
# Vehicle definition
# =================================
@process
def Vehicle(env, c_in, c_out):
    while True:
        receiving = c_in.receive() 
        _tote = yield env.execute(receiving) #waiting until something is received
        d = dv * (_tote.column + 1) #distance to tote
        t = traveltimevehicle(d, vmaxv, av) #computing travel time
        yield env.timeout(2*t + 2*lv) #waiting traviling time + unloading and loading time  
        sending = c_out.send(receiving.entity) #sending out the received entity 
        yield env.execute(sending) 

# =================================
# Main
# =================================
def model(verbose : bool = True):
    env = Environment()
    a = Channel(env)
    b = Channel(env)
    c = Channel(env)
    G = Generator(env, a)
    D = Demand_Buffer(env, a,b)
    V = Vehicle(env, b, c)
    E = Exit(env, c, verbose)
    env.run(until=E)
    if verbose:
        print ("simulation has ended")

# =================================
# Main
# =================================
model()


tote =      1;  Entrytime =     0.0000;  Column = 11;  Mean throughput =0.058824  Mean flowtime = 17.0000
tote =      2;  Entrytime =    45.9880;  Column = 38;  Mean throughput =0.033268  Mean flowtime = 15.5650
tote =      3;  Entrytime =    45.9880;  Column = 38;  Mean throughput =0.031540  Mean flowtime = 26.7534
tote =      4;  Entrytime =   138.9438;  Column = 12;  Mean throughput =0.025541  Mean flowtime = 24.4817
tote =      5;  Entrytime =   306.0582;  Column = 39;  Mean throughput =0.014632  Mean flowtime = 26.7187
tote =      6;  Entrytime =   549.4010;  Column = 11;  Mean throughput =0.010593  Mean flowtime = 25.0989
tote =      7;  Entrytime =   668.2612;  Column = 23;  Mean throughput =0.010097  Mean flowtime = 25.0848
tote =      8;  Entrytime =   850.1188;  Column = 30;  Mean throughput =0.009093  Mean flowtime = 25.6575
tote =      9;  Entrytime =   991.9169;  Column =  5;  Mean throughput =0.008956  Mean flowtime = 24.2511
tote =     10;  Entrytime =  1118.9056;  Colum

tote =    666;  Entrytime =  47553.7412;  Column = 29;  Mean throughput =0.014001  Mean flowtime = 29.1124
tote =    667;  Entrytime =  47553.7412;  Column = 29;  Mean throughput =0.014014  Mean flowtime = 29.1332
tote =    668;  Entrytime =  47729.4118;  Column =  7;  Mean throughput =0.013991  Mean flowtime = 29.1111
tote =    669;  Entrytime =  47774.1814;  Column =  8;  Mean throughput =0.013999  Mean flowtime = 29.0900
tote =    670;  Entrytime =  47825.4723;  Column = 28;  Mean throughput =0.014003  Mean flowtime = 29.0784
tote =    671;  Entrytime =  47825.4723;  Column = 28;  Mean throughput =0.014016  Mean flowtime = 29.1091
tote =    672;  Entrytime =  47825.4723;  Column = 28;  Mean throughput =0.014028  Mean flowtime = 29.1819
tote =    673;  Entrytime =  47908.6390;  Column = 54;  Mean throughput =0.014041  Mean flowtime = 29.1729
tote =    674;  Entrytime =  47934.9443;  Column = 38;  Mean throughput =0.014048  Mean flowtime = 29.1928
tote =    675;  Entrytime =  47934.94

tote =    896;  Entrytime =  64159.9998;  Column = 12;  Mean throughput =0.013961  Mean flowtime = 28.8724
tote =    897;  Entrytime =  64257.5732;  Column =  6;  Mean throughput =0.013956  Mean flowtime = 28.8555
tote =    898;  Entrytime =  64369.3557;  Column = 40;  Mean throughput =0.013943  Mean flowtime = 28.8628
tote =    899;  Entrytime =  64427.0377;  Column = 23;  Mean throughput =0.013951  Mean flowtime = 28.8462
tote =    900;  Entrytime =  64456.5612;  Column = 47;  Mean throughput =0.013961  Mean flowtime = 28.8247
tote =    901;  Entrytime =  64495.6227;  Column = 32;  Mean throughput =0.013967  Mean flowtime = 28.8054
tote =    902;  Entrytime =  64495.6227;  Column = 32;  Mean throughput =0.013976  Mean flowtime = 28.8206
tote =    903;  Entrytime =  64569.3920;  Column = 14;  Mean throughput =0.013981  Mean flowtime = 28.8097
tote =    904;  Entrytime =  64753.4258;  Column = 37;  Mean throughput =0.013953  Mean flowtime = 28.8158
tote =    905;  Entrytime =  64886.87

tote =   1539;  Entrytime =  116685.2332;  Column = 22;  Mean throughput =0.013189  Mean flowtime = 28.6257
tote =   1540;  Entrytime =  116685.2332;  Column = 22;  Mean throughput =0.013195  Mean flowtime = 28.6255
tote =   1541;  Entrytime =  116726.1615;  Column =  4;  Mean throughput =0.013200  Mean flowtime = 28.6150
tote =   1542;  Entrytime =  116828.2561;  Column =  5;  Mean throughput =0.013197  Mean flowtime = 28.6048
tote =   1543;  Entrytime =  117075.0119;  Column =  9;  Mean throughput =0.013178  Mean flowtime = 28.5965
tote =   1544;  Entrytime =  117090.6861;  Column =  3;  Mean throughput =0.013185  Mean flowtime = 28.5855
tote =   1545;  Entrytime =  117261.3703;  Column = 21;  Mean throughput =0.013173  Mean flowtime = 28.5823
tote =   1546;  Entrytime =  117321.3461;  Column = 20;  Mean throughput =0.013175  Mean flowtime = 28.5787
tote =   1547;  Entrytime =  117869.9265;  Column = 19;  Mean throughput =0.013122  Mean flowtime = 28.5746
tote =   1548;  Entrytime = 

tote =   1696;  Entrytime =  127893.9563;  Column = 28;  Mean throughput =0.013258  Mean flowtime = 28.5936
tote =   1697;  Entrytime =  127893.9563;  Column = 28;  Mean throughput =0.013263  Mean flowtime = 28.6115
tote =   1698;  Entrytime =  128016.4200;  Column =  5;  Mean throughput =0.013263  Mean flowtime = 28.6023
tote =   1699;  Entrytime =  128189.7165;  Column = 45;  Mean throughput =0.013250  Mean flowtime = 28.6088
tote =   1700;  Entrytime =  128271.7774;  Column = 50;  Mean throughput =0.013252  Mean flowtime = 28.5971
tote =   1701;  Entrytime =  128296.2552;  Column = 29;  Mean throughput =0.013256  Mean flowtime = 28.5963
tote =   1702;  Entrytime =  128296.2552;  Column = 29;  Mean throughput =0.013260  Mean flowtime = 28.6125
tote =   1703;  Entrytime =  128296.2552;  Column = 29;  Mean throughput =0.013265  Mean flowtime = 28.6457
tote =   1704;  Entrytime =  128486.4979;  Column = 55;  Mean throughput =0.013261  Mean flowtime = 28.6376
tote =   1705;  Entrytime = 

...

tote =   8142;  Entrytime =  585089.2207;  Column = 19;  Mean throughput =0.013915  Mean flowtime = 28.4692
tote =   8143;  Entrytime =  585089.2207;  Column = 19;  Mean throughput =0.013916  Mean flowtime = 28.4730
tote =   8144;  Entrytime =  585089.2207;  Column = 19;  Mean throughput =0.013917  Mean flowtime = 28.4795
tote =   8145;  Entrytime =  585253.6242;  Column = 19;  Mean throughput =0.013917  Mean flowtime = 28.4764
tote =   8146;  Entrytime =  585263.6240;  Column = 50;  Mean throughput =0.013918  Mean flowtime = 28.4749
tote =   8147;  Entrytime =  585263.6240;  Column = 50;  Mean throughput =0.013919  Mean flowtime = 28.4786
tote =   8148;  Entrytime =  585491.0312;  Column =  8;  Mean throughput =0.013916  Mean flowtime = 28.4760
tote =   8149;  Entrytime =  585491.0312;  Column =  8;  Mean throughput =0.013918  Mean flowtime = 28.4753
tote =   8150;  Entrytime =  585538.6017;  Column = 42;  Mean throughput =0.013919  Mean flowtime = 28.4722
tote =   8151;  Entrytime = 

tote =   8775;  Entrytime =  630167.5843;  Column =  9;  Mean throughput =0.013925  Mean flowtime = 28.5146
tote =   8776;  Entrytime =  630281.7738;  Column = 38;  Mean throughput =0.013923  Mean flowtime = 28.5153
tote =   8777;  Entrytime =  630513.5361;  Column = 13;  Mean throughput =0.013920  Mean flowtime = 28.5138
tote =   8778;  Entrytime =  630513.5361;  Column = 13;  Mean throughput =0.013921  Mean flowtime = 28.5143
tote =   8779;  Entrytime =  630591.0056;  Column = 45;  Mean throughput =0.013921  Mean flowtime = 28.5156
tote =   8780;  Entrytime =  630683.0913;  Column = 19;  Mean throughput =0.013921  Mean flowtime = 28.5135
tote =   8781;  Entrytime =  630709.6708;  Column = 54;  Mean throughput =0.013922  Mean flowtime = 28.5110
tote =   8782;  Entrytime =  630709.6708;  Column = 54;  Mean throughput =0.013923  Mean flowtime = 28.5136
tote =   8783;  Entrytime =  630870.9829;  Column =  4;  Mean throughput =0.013921  Mean flowtime = 28.5141
tote =   8784;  Entrytime = 

tote =   8986;  Entrytime =  645100.8014;  Column = 53;  Mean throughput =0.013929  Mean flowtime = 28.4961
tote =   8987;  Entrytime =  645100.8014;  Column = 53;  Mean throughput =0.013930  Mean flowtime = 28.4996
tote =   8988;  Entrytime =  645234.8206;  Column = 24;  Mean throughput =0.013929  Mean flowtime = 28.4993
tote =   8989;  Entrytime =  645296.1527;  Column = 35;  Mean throughput =0.013929  Mean flowtime = 28.4998
tote =   8990;  Entrytime =  645349.3839;  Column = 53;  Mean throughput =0.013930  Mean flowtime = 28.4990
tote =   8991;  Entrytime =  645378.0880;  Column =  2;  Mean throughput =0.013931  Mean flowtime = 28.5000
tote =   8992;  Entrytime =  645378.0880;  Column =  2;  Mean throughput =0.013932  Mean flowtime = 28.5023
tote =   8993;  Entrytime =  645460.7787;  Column = 50;  Mean throughput =0.013932  Mean flowtime = 28.5039
tote =   8994;  Entrytime =  645546.4885;  Column =  1;  Mean throughput =0.013932  Mean flowtime = 28.5018
tote =   8995;  Entrytime = 

tote =   9597;  Entrytime =  689470.5555;  Column = 29;  Mean throughput =0.013919  Mean flowtime = 28.4892
tote =   9598;  Entrytime =  689470.5555;  Column = 29;  Mean throughput =0.013920  Mean flowtime = 28.4924
tote =   9599;  Entrytime =  689645.3711;  Column = 13;  Mean throughput =0.013918  Mean flowtime = 28.4914
tote =   9600;  Entrytime =  689763.3707;  Column =  7;  Mean throughput =0.013918  Mean flowtime = 28.4899
tote =   9601;  Entrytime =  689784.7123;  Column = 40;  Mean throughput =0.013918  Mean flowtime = 28.4907
tote =   9602;  Entrytime =  689909.5832;  Column = 15;  Mean throughput =0.013917  Mean flowtime = 28.4898
tote =   9603;  Entrytime =  690042.1665;  Column = 40;  Mean throughput =0.013916  Mean flowtime = 28.4906
tote =   9604;  Entrytime =  690222.7799;  Column = 44;  Mean throughput =0.013914  Mean flowtime = 28.4907
tote =   9605;  Entrytime =  690222.7799;  Column = 44;  Mean throughput =0.013914  Mean flowtime = 28.4948
tote =   9606;  Entrytime = 

tote =   9788;  Entrytime =  703522.4034;  Column = 20;  Mean throughput =0.013912  Mean flowtime = 28.4681
tote =   9789;  Entrytime =  703565.2826;  Column =  9;  Mean throughput =0.013913  Mean flowtime = 28.4668
tote =   9790;  Entrytime =  703607.7438;  Column = 35;  Mean throughput =0.013913  Mean flowtime = 28.4673
tote =   9791;  Entrytime =  703657.7941;  Column = 48;  Mean throughput =0.013914  Mean flowtime = 28.4686
tote =   9792;  Entrytime =  703881.8933;  Column = 26;  Mean throughput =0.013911  Mean flowtime = 28.4685
tote =   9793;  Entrytime =  704021.5634;  Column = 49;  Mean throughput =0.013909  Mean flowtime = 28.4699
tote =   9794;  Entrytime =  704083.5221;  Column = 25;  Mean throughput =0.013910  Mean flowtime = 28.4697
tote =   9795;  Entrytime =  704185.9096;  Column = 19;  Mean throughput =0.013910  Mean flowtime = 28.4669
tote =   9796;  Entrytime =  704185.9096;  Column = 19;  Mean throughput =0.013911  Mean flowtime = 28.4665
tote =   9797;  Entrytime = 

f. Confirm that your simulations produce the correct throughput and flow time.

Answer: 

Using our troughput analysis function we can see that the mean trouhgput has not changed. 

The mean flow time of the simulation is a bit higher than the mean flow time of the lift, this is because of the fact that there now is the possibility of a product being in the buffer and having to wait for the lift.

In [72]:
troughputanalysis(12)

Min mean troughput = 0.013930, Max mean troughput = 0.014352
Standard deviation mean troughput = 0.000112
95% confidence interval mean troughput 0.014238 +/- 0.000063
 
Min mean flowtime = 27.585170, Max mean flowtime = 28.570954
Standard deviation mean flowtime = 0.284960
95% confidence interval mean flowtime 28.095160 +/- 0.161231


g.  Run your simulation at least 10 times. What is the range of outcomes for the mean throughput? Determine (roughly, by trial and error) the number of orders required to get good estimates for the flow time (first three non-zero digits are correct).

Answer: 

As can be seen in the troughputanalysis that about 12 runs are needed to get a 3 digit accurate estimate of the mean flow time



## 6.5 Exercise 5: Lift as two stage machine (5 points)
In the previous exercises we focussed on modeling a tier. In exercises 5-8 we focus on modeling the Buffer and Lift, starting with the Lift. We model the Lift as a machine, which repeatedly does the following: request a destination tier, move to the desired tier, receive a tote (first delay for `ll`, then communicate), move to the ground floor, deliver the tote (first delay for `ll`, then communicate). In this exercise we assume that moving to the desired tier takes 23.0 seconds, receiving the tote takes 2.0 seconds, moving to the ground floor again takes 23.0 seconds, and delivering the tote also takes 2.0 seconds. Note that, in this case, this implies that the tote should leave the Generator and enter the Lift 25.0 seconds after the Lift has received the destination tier. All of these times are assumed to be deterministic.

a. Assume that after 1.0 second the first tote arrives. Subsequently a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job spends in the Generator, and spends in the Lift.

Answer: 

G is time spend in generator and L is time spend in the lift
<img src="figures/6,5.png" alt="drawing" width="800"/> 



b. Complete the simulation code in the template below, incorporating the actual time a vehicle requires for picking up a tote and delivering it to the buffer.

In [73]:
# =================================
# Tote definition
# =================================
@dataclass
class Tote:
    entrytime: float = 0
    tier: int = 0

# =================================
# Global Lift variables
# =================================
ll = 2.0  # time to load/unload the lift


# =================================
# Generator
# =================================
@process
def Generator(env, c_out, c_lift, verbose : bool = True):
    delays=[1.0, 10.0, 100.0, 100.0]
    while len(delays)>0:
        yield env.timeout(delays[0])
        delays = delays[1:]
        yield env.execute(c_lift.send(1))
        if verbose:
            print(f"Generator: Informed Lift to go to tier 1 at time {env.now:3.1f}");
        x = Tote(entrytime = env.now, tier = 1)
        yield env.execute(c_out.send(x))
        if verbose:
            print(f"Generator: Tote has completely left the Generator and entered "
                  f"the Lift at time {env.now:3.1f}")
    yield env.timeout(100.0)


# =================================
# Lift
# =================================
@process
def Lift(env, c_in, c_lift, c_out):
    while True:
        _tier = yield env.execute(c_lift.receive())
        yield env.timeout(23 + ll)

        _tote = yield env.execute(c_in.receive())
        yield env.timeout(23 + ll)

        yield env.execute(c_out.send(_tote))
    
# =================================
# Exit 
# =================================
@process
def Exit(env, c_in, verbose : bool = True):
    while True:
        _Tote = yield env.execute(c_in.receive())
        if verbose:
            print(f"Exit: Tote from tier {_Tote.tier} has completely left the Lift and has been received "
                  f"by the Exit at time {env.now:3.1f}");

# =================================
# Model
# =================================
def model(verbose : bool = True):
    env = Environment()
    a = Channel(env)  # for sending lots
    b = Channel(env)  # lift tier
    c = Channel(env)  # for sending lots
    G = Generator(env, a, b, verbose)
    L = Lift(env, a, b, c)
    E = Exit(env, c, verbose)
    env.run()
    if verbose:
        print ("simulation has ended")

# =================================
# Main
# =================================
model()

Generator: Informed Lift to go to tier 1 at time 1.0
Generator: Tote has completely left the Generator and entered the Lift at time 26.0
Generator: Informed Lift to go to tier 1 at time 51.0
Exit: Tote from tier 1 has completely left the Lift and has been received by the Exit at time 51.0
Generator: Tote has completely left the Generator and entered the Lift at time 76.0
Exit: Tote from tier 1 has completely left the Lift and has been received by the Exit at time 101.0
Generator: Informed Lift to go to tier 1 at time 176.0
Generator: Tote has completely left the Generator and entered the Lift at time 201.0
Exit: Tote from tier 1 has completely left the Lift and has been received by the Exit at time 226.0
Generator: Informed Lift to go to tier 1 at time 301.0
Generator: Tote has completely left the Generator and entered the Lift at time 326.0
Exit: Tote from tier 1 has completely left the Lift and has been received by the Exit at time 351.0
simulation has ended


c. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram.

Answer: 

The same generator and exit times are observed in the model as in the lot-time-diagram 

## 6.6 Exercise 6: Buffer with only one tier (5 points)
In case we have only one tier, we could use a standard model for a finite buffer. However, keeping in mind that we need to model in the next exercise Level finite buffers in parallel where totes are served at a first-come-first-serve basis, we model the finite buffer slightly differently. We have a counter `n` which counts the number of jobs in the buffer, and we keep a list `xs` of totes that have arrived to the buffer. As long as the buffer contains less than `bc` totes, the buffer can receive jobs. Furthermore, if the buffer contains totes, it is possible to receive a request from the Lift (asking for which tier to move to, which is always 0 in this case). Additionally, if the buffer contains totes it is possible to send the first tote of the list `xs` to the lift.

a. Assume that after 1.0 second the first tote arrives. Subsequently, a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job spends in the Generator, in the Buffer, and spends in the Lift.

Answer: 

G is time spend in generator and L is time spend in the lift and B time spend in the buffer
<img src="figures/6,6.png" alt="drawing" width="800"/> 


 b. Complete the simulation code in the template below, only the Generator and Buffer need to be redefined.

In [74]:
# =================================
# Global Lift variables
# =================================
ll = 2.0  # time to load/unload the lift
bc = 1    # buffer capacity

# =================================
# Generator
# =================================
@process
def Generator(env, c_out, verbose : bool = True):
    delays=[1.0, 10.0, 100.0, 100.0]
    while len(delays)>0:
        yield env.timeout(delays[0])
        delays = delays[1:]
        x = Tote(entrytime = env.now, tier = 0)
        yield env.execute(c_out.send(x))
        if verbose:
            print(f"Generator: sending tote to Buffer at time {env.now:3.1f}")
    yield env.timeout(100.0)

# =================================
# Buffer
# =================================
@process
def Buffer(env, c_in, c_out, c_lift):
    xs = [] # list of jobs
    n = 0
    while True:
        receiving = c_in.receive() if n < bc else None
        call_lift = c_lift.send(xs[0].tier) if len(xs) > 0 else None
        sending   = c_out.send(xs[0]) if len(xs)>0 else None
        
        yield env.select(receiving, call_lift, sending)

        if selected(receiving):
            x = receiving.entity
            xs = xs + [x]
            n = n+1
        
        if selected(call_lift):
            pass
        
        if selected(sending):
            xs = xs[1:]
            n = n - 1
            
# =================================
# Model
# =================================
def model(verbose : bool = True):
    env = Environment()
    a = Channel(env)  # for sending lots
    b = Channel(env)  # for sending lots
    c = Channel(env)  # for calling the lift
    d = Channel(env)  # for sending lots

    G = Generator(env, a, verbose)
    B = Buffer(env, a, b, c)
    L = Lift(env, b, c, d)
    E = Exit(env, d, verbose)
    env.run()
    if verbose:
        print ("simulation has ended")

# =================================
# Main
# =================================
model()

Generator: sending tote to Buffer at time 1.0
Generator: sending tote to Buffer at time 26.0
Exit: Tote from tier 0 has completely left the Lift and has been received by the Exit at time 51.0
Exit: Tote from tier 0 has completely left the Lift and has been received by the Exit at time 101.0
Generator: sending tote to Buffer at time 126.0
Exit: Tote from tier 0 has completely left the Lift and has been received by the Exit at time 176.0
Generator: sending tote to Buffer at time 226.0
Exit: Tote from tier 0 has completely left the Lift and has been received by the Exit at time 276.0
simulation has ended


c. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram

Answer: 

The same buffer receive and exit times are observed in the model as in the lot-time-diagram 

## Exercise 7: Buffer with multiple tiers (5 points)
We extend the buffer from the previous exercise to `Level` parallel finite buffers of size `bc` which are modelled as a list of `Level` counters. For this list we use the variable `n`. We keep a common list `xs` of totes that have arrived to all buffers. This list is used to determine which tote should be picked up first by the Lift. For each of the tiers it holds that if the buffer of that tier is not full yet, a tote can be received. Furthermore, if the buffer contains totes, it is possible to receive a request from the Lift asking for the tier to move to. Additionally, if the buffer contains totes it is possible to send the first tote of the list `xs` to the lift.

a. Consider two tiers, and assume that after `Tier` seconds the first tote arrives (for two tiers: after 0.0 for tier 0 and
after 1.0 for tier 1). Subsequently a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion
of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job
spends in which Generator, in the Buffer, and spends in the Lift.

Answer: 

G is time spend in generator and L is time spend in the lift and B1 time spend in the first buffer and B2 time sepnd in the second buffer
<img src="figures/6,7.png" alt="drawing" width="800"/> 

b. Complete the simulation code in the template below.

In [75]:
# =================================
# Global variables
# =================================
ll = 2.0  # time to load/unload the lift
bc = 1    # buffer capacity
Level = 2 # the number of tiers

# =================================
# Generator
# =================================
@process
def Generator(env, c_out, level):
    delays=[1.0*level, 10.0, 100.0, 100.0]
    while len(delays)>0:
        yield env.timeout(delays[0])
        print(f"Generator {level:d}: Generated tote at "
              f"time {env.now:3.1f}")
        delays = delays[1:]
        x = Tote(entrytime = env.now, tier = level)
        yield env.execute(c_out.send(x))
        print(f"Generator {level:d}: Sending tote to Buffer completed at "
              f"time {env.now:3.1f}")
    yield env.timeout(100.0)
    
# =================================
# Buffer
# =================================
@process
def Buffer(env, c_in, c_out, c_lift):
    global buffer_in_rate
    xs = [] #FIFO totes
    n = [0] * Level #How many totes in each buffer

    while True:
        receiving = [c_in[Tier].receive() if n[Tier] < bc else None for Tier in range(Level)]
        call_lift = c_lift.send(xs[0].tier) if len(xs) > 0 else None
        sending = c_out.send(xs[0]) if len(xs) > 0 else None
        communications = receiving + [call_lift] + [sending]

        yield env.select(*communications)
        
        for Tier in range(Level):
            if selected(receiving[Tier]):
                _tote = receiving[Tier].entity
                xs = xs + [_tote]
                n[Tier] = n[Tier] + 1
                
        if selected(call_lift):
            pass
            
        if selected(sending):
            tier = xs[0].tier
            if n[tier] > 0:
                n[tier] = n[tier] - 1 #removing the tote from the buffer counter
            xs = xs[1:] #removing tote from the fifo buffer
            print(n)

            
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = [Channel(env) for tier in range(Level)] # a channel for each tier (sending lots)
    b = Channel(env)  # for sending lots
    c = Channel(env)  # for calling the lift
    d = Channel(env)  # for sending lots
    Gs = [Generator(env, a[tier], tier) for tier in range(Level)] 
    B = Buffer(env, a, b, c)
    L = Lift(env, b, c, d)
    E = Exit(env, d)
    env.run(until=1000000)
    print ("simulation has ended")

# =================================
# Main
# =================================
model()


Generator 0: Generated tote at time 0.0
Generator 0: Sending tote to Buffer completed at time 0.0
Generator 1: Generated tote at time 1.0
Generator 1: Sending tote to Buffer completed at time 1.0
Generator 0: Generated tote at time 10.0
Generator 1: Generated tote at time 11.0
Generator 0: Sending tote to Buffer completed at time 25.0
Exit: Tote from tier 0 has completely left the Lift and has been received by the Exit at time 50.0
Generator 1: Sending tote to Buffer completed at time 75.0
Exit: Tote from tier 1 has completely left the Lift and has been received by the Exit at time 100.0
Generator 0: Generated tote at time 125.0
Generator 0: Sending tote to Buffer completed at time 125.0
Exit: Tote from tier 0 has completely left the Lift and has been received by the Exit at time 150.0
Generator 1: Generated tote at time 175.0
Generator 1: Sending tote to Buffer completed at time 175.0
Exit: Tote from tier 1 has completely left the Lift and has been received by the Exit at time 200.0
G

c. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram

Answer: ...

The same generator and exit times are observed in the model as in the lot-time-diagram 

## Exercise 8: Lift accurately modelled (5 points)

Assume that the Lift starts from the ground floor. If it has to go to level $i \in \{0, Level - 1\}$, it needs to travel a
distance $dl \cdot (i + 1)$, pick up the tote, travel back, and deliver the tote at the ground floor. For traveling the required
distance, the vehicle first goes with a constant acceleration `al` *m/s$^2$* until it reaches its maximum velocity `vmaxl`, then
it moves with this velocity and decelerates with a constant deceleration `al` to approach its destination tier. If the tier
is located too close to the ground floor, it is possible that the Lift will not reach its maximum speed.

a. From this information, (analytically) determine the time (in seconds) it takes the Lift to a given tier.

Answer:

This excercise is the same as excercise 4 only now it is not the driving speed but the elevating speed that is considered. 

If the lift will not reach its max speed, then: 
$ t_{1} = 2\sqrt{\frac{dl(i + 1)}{al}} $ 
- for $ dl(i + 1) \leq \frac{vmaxl\ ^2}{al} $

If the lift will reach its maximum speed then: 
$ t_{2} = \frac{2\cdot\ vmaxl}{al} + \frac{dl(i + 1)-\frac{vmaxl\ ^2}{al}}{vmaxl} $
- for $ dl(i + 1) > \frac{vmaxl\ ^2}{al} $



b. Next, if loading and unloading a tote both take `ll` seconds, determine (analytically) the time it takes the Lift to pick up a tote from tier $i \in \{0, depth - 1\}$ and deliver it to the buffer.

Answer: 

This excercise is the same as excercise 4 only now it is not the driving speed but the elevating speed that is considered.

If the lift will not reach its max speed, then: 
$ t_{1} = 4\sqrt{\frac{dl(i + 1)}{al}} + 2ll $ 
- for $ dl(i + 1) \leq \frac{vmaxl\ ^2}{al} $

If the lift will reach its maximum speed then: 
$ t_{2} = 2(\frac{2\cdot\ vmaxl}{al} + \frac{dl(i + 1)-\frac{vmaxl\ ^2}{al}}{vmaxl} + lv) $
- for $ dl(i + 1) > \frac{vmaxl\ ^2}{al} $

Again the boundaries can also be refined by filling in values and solving for i in: 
$ i = \frac{vmaxl\ ^2}{al \cdot dl} - 1 = \frac{5.0^2}{7.0 \cdot 0.8} - 1 = 3.46 $

Following the same reasoning as before, the maximum speed of the lift will only be reached when heading to level 4 or higher.


c. Consider two tiers, and assume that after Tier seconds the first tote arrives (for two tiers: after 0.0 for tier 0 and after 1.0 for tier 1). Subsequently a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job spends in which Generator, in the Buffer, and spends in the Lift.

Answer: 
G is time spend in generator and L is time spend in the lift and B1 time spend in the first buffer and B2 time sepnd in the second buffer
<img src="figures/6,8.png" alt="drawing" width="800"/>  

d. Complete the simulation code in the template below.

In [108]:
# =================================
# Global variables
# =================================
ll = 2.0        # time to load/unload the lift
bc = 1          # buffer capacity
Level = 2       # the number of tiers
dl = 0.8        # unit height clearance
vmaxl = 5.0     # maximum velocity of lift
al = 7.0        # acceleration/deceleration of lift

# =================================
# Lift definition
# =================================
@process
def Lift(env, c_in, c_lift, c_out):
    while True:
        calling = c_lift.receive() 
        tier = yield env.execute(calling) #waiting for the elevator to be called
        
        d = dl * (tier + 1) #distance to tote
        t = traveltimevehicle(d, vmaxl, al) #reusing the traveltime vehicle function
        
        yield env.timeout(t + ll) #travelling to tote 
        receiving = c_in.receive()
        _tote = yield env.execute(receiving) #receiving tote
        #print(f"Lift: receiving tote from tier {_tote.tier} at {env.now:3.1f}")
        
        yield env.timeout(t + ll) #traveling back
        sending = c_out.send(receiving.entity) #sending out the received entity 
        yield env.execute(sending) 
        
        
        
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = [Channel(env) for Tier in range(Level)] # a channel for each tier, each sending totes
    b = Channel(env)  # for sending totes
    c = Channel(env)  # for calling the lift
    d = Channel(env)  # for sending totes

    Gs = [Generator(env, a[Tier], Tier) for Tier in range(Level)] 
    B = Buffer(env, a, b, c)
    L = Lift(env, b, c, d)
    E = Exit(env, d)
    env.run()
    print ("simulation has ended")

    
# =================================
# Main
# =================================
model()

ZeroDivisionError: float division by zero

e. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram

Answer:

The same generation and exit times can be seen, however the lift is significantly faster than before



## 6.9 Exercise 9: Entire system (10 points)
In the previous exercises we developed and tested each process individually. Now it is time to combine all processes into one model.

a. Determine the (total) arrival rate of orders for a system with `Level` tiers, where for each tier orders arrive with a mean inter arrival time of `arrive`.

Answer: 


$ \text{(total) arrival rate of orders} = \frac{\text{Level}}{\text{arrive}} = \frac{9}{70} = 0.13 \text{ totes per second.} $


b. Complete the simulation code in the template below by substituting the code for the processes as you derived in Exercises 1, 2, 4, 7, and 8. Note that the type tote has been extended in comparison with Exercise 1, so one line of code extra is required in the Generator process to include the tier.

In [144]:
# =================================
# Tote
# =================================
@dataclass
class Tote:
    entrytime: float = 0.0
    column: int = 0
    tier: int  = 0
        
# =================================
# Global variables
# =================================
lv = 3.0                   # time to load/unload the vehicle
dv = 0.5                   # unit width clearance
vmaxv = 1.5                # maximum velocity of the vehicle
av = 1.0                   # acceleration/deceleration of the vehicle
ll = 2.0                   # time to load/unload the lift
dl = 0.8                   # unit height clearance
vmaxl = 5.0                # maximum velocity of lift
al = 7.0                   # acceleration/deceleration of lift
bc = 1                     # buffer capacity
arrive = 70.0              # inter arrival time of requests
Level = 9                  # the number of tiers
depth  = 55                # the number of columns
number_of_orders = 20000  # the number of orders to process

# =================================
# Generator
# =================================
@process
def Generator(env, c_out, Tier):
    while True:
        x = Tote()
        x.entrytime = env.now
        x.column =  random.randint(0, depth) 
        x.tier = random.randint(0, Level) 
        yield env.execute(c_out.send(x))
        delay = random.exponential(arrive)
        yield env.timeout(delay)
        
        
# =================================
# Demand Buffer
# =================================
@process
def Demand_Buffer(env, c_in, c_out):
    xs = [] # list of totes
    while True:
        sending = c_out.send(xs[0]) if len(xs)>0 else None
        receiving = c_in.receive()
        x = yield env.select(sending, receiving)
        if selected(receiving):
            xs = xs + [x]
        if selected(sending):
            xs = xs[1:]
                 
# =================================
# Vehicle
# =================================
@process
def Vehicle(env, c_in, c_out):
    while True:
        receiving = c_in.receive() 
        _tote = yield env.execute(receiving) #waiting until something is received
        d = dv * (_tote.column + 1) #distance to tote
        t = traveltimevehicle(d, vmaxv, av) #computing travel time
        yield env.timeout(t + 2*lv) #waiting traviling time + unloading and loading time  
        sending = c_out.send(receiving.entity) #sending out the received entity 
        yield env.execute(sending) 

# =================================
# Buffer
# =================================
buffer_in_rate = 0
@process
def Buffer(env, c_in, c_out, c_lift):
    global buffer_in_rate
    xs = [] #FIFO totes
    n = [0] * Level #How many totes in each buffer
    n_totes_trough = 0
    while True:
        receiving = [c_in[Tier].receive() if n[Tier] < bc else None for Tier in range(Level)]
        call_lift = c_lift.send(xs[0].tier) if len(xs) > 0 else None
        sending = c_out.send(xs[0]) if len(xs) > 0 else None
        communications = receiving + [call_lift] + [sending]

        yield env.select(*communications)
        
        for Tier in range(Level):
            if selected(receiving[Tier]):
                n_totes_trough += 1
                buffer_in_rate = n_totes_trough / env.now
                _tote = receiving[Tier].entity
                xs = xs + [_tote]
                n[Tier] = n[Tier] + 1
                
        if selected(call_lift):
            pass
            
        if selected(sending):
            _tier = xs[0].tier
            n[_tier] = n[_tier] - 1 #removing the tote from the buffer counter
            xs = xs[1:] #removing tote from the fifo buffer
       

            
# =================================
# Lift
# =================================
@process
def Lift(env, c_in, c_lift, c_out):
    while True:
        calling = c_lift.receive()
        tier = yield env.execute(calling) #waiting for a call
        
        d = dl * (tier + 1) #distance to tote
        t = traveltimevehicle(d, vmaxl, al) #reusing the traveltime vehicle function
        yield env.timeout(t + ll) #waiting traviling time + loading time  
        
        receiving = c_in.receive() 
        _tote = yield env.execute(receiving) #receiving tote
        
        yield env.timeout(t + ll) #travel time and unloading time
 
        sending = c_out.send(receiving.entity) #sending out the received entity 
        yield env.execute(sending) 
        
# =================================
# Exit
# =================================
@process
def Exit(env, c_in, verbose : bool = True):
    mphi = 0.0
    Collumns = set()
    Tiers = set() 
    
    for i in range(1, number_of_orders + 1):
        x = yield env.execute(c_in.receive())
        Collumns.add(x.column)
        Tiers.add(x.tier)
        mphi = (i - 1) / i * mphi + (env.now - x.entrytime) / i
        mthi = i/env.now
    if verbose:
        print(Tiers)
        print(Collumns)
    return mphi, mthi 


            
        
# =================================
# GDV
# =================================
def GDV(env, c_out, Tier):
    a = Channel(env)  # for sending totes
    b = Channel(env)  # for sending totes
    G = Generator(env, a, Tier)
    D = Demand_Buffer(env, a,b)
    V = Vehicle(env, b, c_out)
        

# =================================
# Model
# =================================
def model(verbose : bool = True):
    env = Environment()
    c = [Channel(env) for Tier in range(Level)] # a channel for each tier, each sending totes
    d = Channel(env)  # for sending totes
    e = Channel(env)  # for calling the lift
    f = Channel(env)  # for sending totes
    GDVs = [ GDV(env, c[Tier], Tier)  for Tier in range(Level) ] 
    B = Buffer(env, c, d, e)
    L = Lift(env, d, e, f)
    E = Exit(env, f, verbose)
    env.run(until=E)
    mph, mth = E.value
    if verbose:
        print(f"--- Mean throughput = {mth:8.6f}; Mean flowtime = {mph:6.4f} ---")
    return mph, mth

# =================================
# Main
# =================================
mph, mth = model()
print(f'Start rate = {buffer_in_rate}')

{0, 1, 2, 3, 4, 5, 6, 7, 8}
{0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54}
--- Mean throughput = 0.120888; Mean flowtime = 5136.0401 ---
Start rate = 0.12092063036056246


c. Verify if the throughput in your simulations matches with the start rate you determined. Verify that totes reach the exit from each tier. Also verify that totes are generated from each column.

Answer: 

As can be seen from the two sets that have been printed after the exit a product has come from every tier and column

The start rate is more difficult to determine as the only point where all the totes are together is in the buffer of the lift. Here the arrival rate is 0.12 which is a bit lower than the order arrival rate but to be expected as the vehicle lowers the rate a tiny bit.



d. Run your simulation 30 times, and record for each run the resulting average throughput and average flow time.
Determine the mean and the standard deviation of both the average throughput and the average flow time for these 30 simulations. Finally, determine a 95% confidence interval for both the average throughput and the average flow time.

Answer: ...



In [130]:
def troughputanalysis(n, verbose: bool = True):
    troughputes = list()
    flowtimes = list()
    for i in range(n):
        print(i)
        #doing multiple runs of the model
        mph, mth = model(False)
        troughputes.append(mth)
        flowtimes.append(mph)
    
    stdev_th = statistics.stdev(troughputes)
    stdev_ph = statistics.stdev(flowtimes)
    if verbose:
        print(f'Min mean troughput = {min(troughputes):8.6f}, Max mean troughput = {max(troughputes):8.6f}')
        print(f'Standard deviation mean troughput = {stdev_th:8.6f}')
        print(f'95% confidence interval mean troughput {statistics.mean(troughputes):8.6f} +/- {1.96 * stdev_th / sqrt(n):8.6f}')
        print(' ')
        print(f'Min mean flowtime = {min(flowtimes):8.6f}, Max mean flowtime = {max(flowtimes):8.6f}')
        print(f'Standard deviation mean flowtime = {stdev_ph:8.6f}')
        print(f'95% confidence interval mean flowtime {statistics.mean(flowtimes):8.6f} +/- {1.96 * stdev_ph / sqrt(n):8.6f}')
    
    return troughputes, flowtimes

In [79]:
x, y = troughputanalysis(30, True)

Min mean troughput = 0.106553, Max mean troughput = 0.113088
Standard deviation mean troughput = 0.001706
95% confidence interval mean troughput 0.109757 +/- 0.000611
 
Min mean flowtime = 2256.608996, Max mean flowtime = 7812.264927
Standard deviation mean flowtime = 1607.368788
95% confidence interval mean flowtime 4492.359369 +/- 575.189534


## 6.10 Exercise 10: Effect of buffer capacity (10 points)
Via computer simulation analyze the impact of the buffer capacity on the throughput and flow time (choose values of `bc` as 1,2,3,200). For each setting, run your simulations 30 times and determine both mean and standard deviation of the resulting average throughput and average flow time for these 30 simulations, as well as 95% confidence intervals.

Answer:

The code in the cell bellow is used to determine the properties of each buffer configuration, in the tables the results can be seen.

| Buffer capacity | 1 | 2 | 3 | 200 | 
| - | - | - | - | - |
| Mean flow time | 4238.11 | 3752.86 | 3649.25 | 29.87 |
| $\sigma$ | 1162.06 | 1207.66 | 1270.03 | 0.32 | 
| 95% confidence interval | 415.84 | 432.16 | 454.47 | 0.12 |

| Buffer capacity | 1 | 2 | 3 | 200 | 
| - | - | - | - | - |
| Mean throughput | 0.109551 | 0.110174 | 0.110705 | 0.115384   |
| $\sigma$ | 0.001730 | 0.001460 | 0.001735 | 0.000602  |
| 95% confidence interval | 0.000619 | 0.000523 | 0.000621 | 0.000215 |



In [80]:
bcs = [1,2,3,200]
arrive = 70

mean_th = str()
mean_ph = str()
_stdev_th = str()
_stdev_ph = str()
th95 = str()
ph95 = str()

n = 30
for i in range(len(bcs)):
    bc = bcs[i]
    
    th, pf = list(), list()
    th, pf = troughputanalysis(n, False)
    
    stdev_th = statistics.stdev(th)
    stdev_ph = statistics.stdev(pf)
    
    #saving strings to make a table
    _stdev_th += f'| {stdev_th:8.6f} '
    _stdev_ph += f'| {stdev_ph:4.2f} '
    mean_th += f'| {statistics.mean(th):8.6f} '
    mean_ph += f'| {statistics.mean(pf):4.2f} '
    th95 += f'| {1.96*stdev_th / sqrt(n):8.6f} '
    ph95 += f'| {1.96*stdev_ph / sqrt(n):4.2f} '
    
print(mean_th)
print(_stdev_th)
print(th95)

print(' ')

print(mean_ph)
print(_stdev_ph)
print(ph95)


| 0.109551 | 0.110174 | 0.110705 | 0.115384 
| 0.001730 | 0.001460 | 0.001735 | 0.000602 
| 0.000619 | 0.000523 | 0.000621 | 0.000215 
 
| 4238.11 | 3752.86 | 3649.25 | 29.87 
| 1162.06 | 1207.66 | 1270.03 | 0.32 
| 415.84 | 432.16 | 454.47 | 0.12 


## 6.11 Exercise 11: Looking for the best layout (30 points)
Via computer simulation consider 6 different scenarios (see the table below) that correspond to different layouts of the
storage facility with a total capacity of 500 totes with different number of tiers and columns.

| Scenario | 1 | 2 | 3 | 4| 5 | 6 |
| - | - | - | - | - | - | - |
| Level |  2 | 5 | 10 | 20 | 25 | 50 |
| Depth | 250 | 100 | 50 | 25 | 20 | 10 |

In order to obtain an answer to the questions below: for each scenario, run your simulations 30 times and determine both mean and standard deviation of the resulting average throughput and average flow time for these 30 simulations, as well as 95% confidence intervals.

a. For each scenario, determine by means of simulation the maximal throughput.

Answer:

The maximal troughput is achieved when the input is completely saturated, meaning that inter arrival time is set low such that the demand buffer is always full. Using the code below the following maximum trouhgputs were deteremined:

| Scenario | 1 | 2 | 3 | 4| 5 | 6 |
| - | - | - | - | - | - | - |
| Max Throughput |  2 | 5 | 10 | 20 | 25 | 50 |



In [ ]:
arrive = 1 #setting the interarrival time high such that the system is fully saturated 
bc = 1
_Levels = [2, 5, 10, 20, 25, 50]
_Depths = [250, 100, 50, 25, 20, 10]

throughputes = str()
number_of_orders = 5000
for i in range(len(_Levels)):
    Level = _Levels[i]
    Depth = _Depths[i]
    
    th, pf = troughputanalysis(n, True)
    throughputes += f'| {mean(th):8.6f} '
    flowtime += f'| {statistics.mean(ph):4.2f} '

0
1
2
3
4
5
6
7
8
9
10
11
12
13


b. Assume a required throughput of 6 totes per minute. Compare the resulting flow time for each feasible scenario.

Answer: 


| Scenario | 1 | 2 | 3 | 4| 5 | 6 |
| - | - | - | - | - | - | - |
| Flow Time |  2 | 5 | 10 | 20 | 25 | 50 |

c. Based on your outcomes, select a layout that seems the best for you. If necessary, introduce other performance indicators and modify the code accordingly. The report on this step should contain an argument to select the best layout.

Answer: ...



## References
[1] G. Marchet, M. Melanci, S. Perotti and E. Tappia, "Analytical model to estimate performance of autonomous vehicle storage and retrieval systems for product totes", International Journal of Production Research, vol. 50(24), 7134-7148, 2012.